In [ ]:
## NOTE: Please add the Roma game next time you scrape: ws_game_id: 1746369 and fbref_id: bca64d25

In [1]:
import soccerdata as sd
import pandas as pd
from tqdm import tqdm
import ScraperFC as sfc
import traceback

import warnings
import numpy as np
import socceraction.spadl as spadl

[04/26/24 08:24:01] INFO     No custom team name replacements found. You can configure these in       ]8;id=452777;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py\_config.py]8;;\:]8;id=345107;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py#87\87]8;;\
                             C:\Users\ksbha\soccerdata\config\teamname_replacements.json.                          

                    INFO     No custom league dict found. You can configure additional leagues in    ]8;id=408294;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py\_config.py]8;;\:]8;id=602267;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_config.py#177\177]8;;\
                             C:\Users\ksbha\soccerdata\config\league_dict.json.                                    

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\pyspark\pandas\__init__.py:50: UserWarning: 'PYARROW_IGNORE_TIMEZONE' environment variable was not set. It is required to set this environment variable to '1' in both driver and executor sides if you use pyarrow>=2.0.0. pandas-on-Spark will set it for you but it does not work if there is a Spark context already launched.
  warnings.warn(


In [2]:
import datetime

In [3]:
## Create a connection to Snowflake
from sqlalchemy import create_engine
import snowflake.connector

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\options.py:103: UserWarning: You have an incompatible version of 'pyarrow' installed (14.0.2), please install a version that adheres to: 'pyarrow<10.1.0,>=10.0.1; extra == "pandas"'
  warn_incompatible_dep(


[04/26/24 08:24:08] WARNING  Failed to import ArrowResult. No Apache Arrow result set format can be    ]8;id=538359;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=693656;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#94\94]8;;\
                             used. ImportError: DLL load failed while importing arrow_iterator: The                
                             specified procedure could not be found.                                               

In [4]:
import snowflake.connector
from snowflake.connector.pandas_tools import write_pandas

In [5]:
pd.set_option('display.max_columns', None)

In [6]:
# spark = SparkSession.builder \
#     .master("local") \
#     .appName("Gegenstats") \
#     .getOrCreate()

In [7]:
scraper = sfc.Understat()
def scrape_league_data(league_years):
    output_df = pd.DataFrame(columns=['№', 'Team', 'M', 'W', 'D', 'L', 'G', 'GA', 'PTS', 'xG', 'NPxG', 'xGA',
       'NPxGA', 'NPxGD', 'PPDA', 'OPPDA', 'DC', 'ODC', 'xPTS', 'season','league'])
    for league_year in league_years:
        try:
            ooper = scraper.scrape_league_table(year=league_year[1], league=league_year[0])
            season_val = league_year[1]
            ooper['season'] = int(str(int(str(season_val)[2:])-1)+str(season_val)[2:])
            if league_year[0] == 'EPL':
                ooper['league'] = 'ENG-Premier League'
            elif league_year[0] == 'La Liga':
                ooper['league'] = 'ESP-La Liga'
            elif league_year[0] == 'Bundesliga':
                ooper['league'] = 'GER-Bundesliga'
            elif league_year[0] == 'Serie A':
                ooper['league'] = 'ITA-Serie A'
            elif league_year[0] == 'Ligue 1':
                ooper['league'] = 'FRA-Ligue 1'
            output_df = pd.concat([output_df, ooper])
            
        except Exception as e:
            print(f"An error occurred for the year {league_years}: {e}")
            traceback.print_exc()
    scraper.close()
    return output_df

league_years = [('EPL', 2024), ('La Liga', 2024), ('Bundesliga', 2024), ('Serie A', 2024), ('Ligue 1', 2024)] 
out = scrape_league_data(league_years)

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\ScraperFC\Understat.py:361: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  columns = pd.read_html(table)[0].columns
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\ScraperFC\Understat.py:366: FutureWarning: Passing literal html to 'read_html' is deprecated and will be removed in a future version. To read from a literal string, wrap it in a 'StringIO' object.
  df = pd.read_html(table)[0]
C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\2348357125.py:20: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  output_df = pd.concat([output_df, ooper])
d:\Users\ksbha\mi

In [8]:
understat_table = out[['league','Team','season', 'W', 'D', 'L','G','GA', 'xG', 'xGA','NPxG','NPxGA','PPDA',
                       'OPPDA','PTS','xPTS']]

In [9]:
understat_table.loc[understat_table['Team'] == 'Arminia Bielefeld', 'Team'] = 'Arminia'
understat_table.loc[understat_table['Team'] == 'Borussia Dortmund', 'Team'] = 'Dortmund'
understat_table.loc[understat_table['Team'] == 'Eintracht Frankfurt', 'Team'] = 'Eint Frankfurt'
understat_table.loc[understat_table['Team'] == 'Greuther Fuerth', 'Team'] = 'Greuther Fürth'
understat_table.loc[understat_table['Team'] == 'Hertha Berlin', 'Team'] = 'Hertha BSC'
understat_table.loc[understat_table['Team'] == 'FC Cologne', 'Team'] = 'Köln'
understat_table.loc[understat_table['Team'] == 'Bayer Leverkusen', 'Team'] = 'Leverkusen'
understat_table.loc[understat_table['Team'] == 'Borussia M.Gladbach', 'Team'] = "M'Gladbach"
understat_table.loc[understat_table['Team'] == 'RasenBallsport Leipzig', 'Team'] = 'RB Leipzig'
understat_table.loc[understat_table['Team'] == 'VfB Stuttgart', 'Team'] = 'Stuttgart'
understat_table.loc[understat_table['Team'] == 'Darmstadt', 'Team'] = 'Darmstadt 98'
understat_table.loc[understat_table['Team'] == 'FC Heidenheim', 'Team'] = 'Heidenheim'

In [10]:
understat_table.loc[understat_table['Team'] == 'Alaves', 'Team'] = 'Alavés'
understat_table.loc[understat_table['Team'] == 'Atletico Madrid', 'Team'] = 'Atlético Madrid'
understat_table.loc[understat_table['Team'] == 'Cadiz', 'Team'] = 'Cádiz'
understat_table.loc[understat_table['Team'] == 'Real Betis', 'Team'] = 'Betis'
understat_table.loc[understat_table['Team'] == 'Real Valladolid', 'Team'] = "Valladolid"
understat_table.loc[understat_table['Team'] == 'Almeria', 'Team'] = 'Almería'

understat_table.loc[understat_table['Team'] == 'Verona', 'Team'] = 'Hellas Verona'
understat_table.loc[understat_table['Team'] == 'Milan', 'Team'] = 'AC Milan'


understat_table.loc[understat_table['Team'] == 'Paris Saint Germain', 'Team'] = "Paris S-G"
understat_table.loc[understat_table['Team'] == 'Saint-Etienne', 'Team'] = "Saint-Étienne"

understat_table.loc[understat_table['Team'] == 'Manchester United', 'Team'] = 'Manchester Utd'
understat_table.loc[understat_table['Team'] == 'Newcastle United', 'Team'] = 'Newcastle Utd'
understat_table.loc[understat_table['Team'] == 'Tottenham Hotspur', 'Team'] = 'Tottenham'
understat_table.loc[understat_table['Team'] == 'Wolverhampton Wanderers', 'Team'] = 'Wolves'
understat_table.loc[understat_table['Team'] == 'Nottingham Forest', 'Team'] = "Nott'ham Forest"
understat_table.loc[understat_table['Team'] == 'Leicester', 'Team'] = 'Leicester City'
understat_table.loc[understat_table['Team'] == 'Leeds', 'Team'] = 'Leeds United'
understat_table.loc[understat_table['Team'] == 'Sheffield United', 'Team'] = "Sheffield Utd"
understat_table.loc[understat_table['Team'] == 'Luton', 'Team'] = 'Luton Town'
understat_table.loc[understat_table['Team'] == 'Norwich', 'Team'] = 'Norwich City'

In [11]:
understat_table.sort_values(by=['league','season','Team'], ascending=True, inplace=True)
understat_table.reset_index(drop=True, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\614021855.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  understat_table.sort_values(by=['league','season','Team'], ascending=True, inplace=True)


In [12]:
understat_table.rename(columns={'Team':'TEAM_NAME', 'W':'TEAM_WINS', 'D':'TEAM_DRAWS', 'league':'COMPETITION',
                                'L': 'TEAM_LOSSES', 'xPTS':'TEAM_XPTS', 'PTS':'TEAM_PTS', 'season':'SEASON',
                                'NPxGA':'NPXG_AGAINST', 'xGA':'XG_AGAINST'}, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\2521636844.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  understat_table.rename(columns={'Team':'TEAM_NAME', 'W':'TEAM_WINS', 'D':'TEAM_DRAWS', 'league':'COMPETITION',


In [13]:
understat_table.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

Get the match data from Snowflake so that we only scrape for matches we don't have yet 

In [14]:
fbref = sd.FBref(leagues=['ENG-Premier League', 'GER-Bundesliga', "ESP-La Liga",
                          'ITA-Serie A', 'FRA-Ligue 1'], seasons=["2324"], no_cache=True)
# fbref = sd.FBref(leagues=["FRA-Ligue 1"], seasons=["2324"], no_cache=True)
fbref_team_standard = fbref.read_team_season_stats(stat_type='standard')
# fbref_team_standard_oppo = fbref.read_team_season_stats(stat_type='standard', opponent_stats=True)
fbref_team_shooting = fbref.read_team_season_stats(stat_type='shooting')
fbref_team_shooting_oppo = fbref.read_team_season_stats(stat_type='shooting', opponent_stats=True)
fbref_team_passing = fbref.read_team_season_stats(stat_type='passing')
fbref_team_passing_oppo = fbref.read_team_season_stats(stat_type='passing', opponent_stats=True)
fbref_team_defense = fbref.read_team_season_stats(stat_type='defense')
fbref_team_possession = fbref.read_team_season_stats(stat_type='possession')
fbref_team_misc = fbref.read_team_season_stats(stat_type='misc')
fbref_keeper = fbref.read_team_season_stats(stat_type='keeper')
fbref_schedule = fbref.read_schedule()
# fbref_lineups = fbref.read_lineup()

[04/26/24 08:28:36] INFO     Saving cached data to C:\Users\ksbha\soccerdata\data\FBref               ]8;id=4367;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py\_common.py]8;;\:]8;id=285008;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py#92\92]8;;\

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:97: UserWarning: You are trying to scrape data for all of the Big 5 European leagues. This can be done more efficiently by setting leagues='Big 5 European Leagues Combined'.
  warnings.warn(
d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


In [15]:
fbref_schedule.loc[fbref_schedule['home_team'] == 'Milan', 'home_team'] = 'AC Milan'
fbref_schedule.loc[fbref_schedule['away_team'] == 'Milan', 'away_team'] = 'AC Milan'

In [16]:
# Convert the date column to datetime format
fbref_schedule['date'] = pd.to_datetime(fbref_schedule['date'])
# fbref_schedule = fbref_schedule[fbref_schedule['date'] < datetime.datetime(2023, 12, 20)]

fbref_schedule = fbref_schedule[fbref_schedule['date'] < datetime.datetime.now().strftime('%Y-%m-%d')]

In [17]:
SNOWFLAKE_USER = 'karan14'
SNOWFLAKE_PASSWORD = 'Snowfl@key0014'
SNOWFLAKE_ACCOUNT = 'lv65293.ca-central-1.aws'
SNOWFLAKE_WAREHOUSE = 'COMPUTE_WH'
SNOWFLAKE_DATABASE = 'GEGENSTATS'
SNOWFLAKE_SCHEMA = 'TABLES'

In [18]:
conn = snowflake.connector.connect(
    user=SNOWFLAKE_USER,
    password=SNOWFLAKE_PASSWORD,
    account=SNOWFLAKE_ACCOUNT,
    warehouse=SNOWFLAKE_WAREHOUSE,
    database=SNOWFLAKE_DATABASE,
    schema=SNOWFLAKE_SCHEMA
)

[04/26/24 10:34:10] INFO     Snowflake Connector for Python Version: 3.3.1, Python Version:       ]8;id=749523;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=23294;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#334\334]8;;\
                             3.11.5, Platform: Windows-10-10.0.22000-SP0                                           

                    INFO     This connection is in OCSP Fail Open Mode. TLS Certificates would   ]8;id=285305;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=320759;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#1103\1103]8;;\
                             be checked for validity and revocation status. Any other                              
                             Certificate Revocation related exceptions or OCSP Responder                           
                             failures would be disregarded in favor of connectivity.                               

                    INFO     Setting use_openssl_only mode to False                              ]8;id=115298;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=692567;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#1121\1121]8;;\

In [19]:
cursor = conn.cursor()

In [20]:
def fetch_data(cursor, query):
    cursor.execute(query)
    rows = cursor.fetchall()
    column_names = [desc[0] for desc in cursor.description]
    return pd.DataFrame(rows, columns=column_names)

In [21]:
df_matches = fetch_data(cursor, 'SELECT * FROM MATCHES')

[04/26/24 10:34:13] INFO     query: [SELECT * FROM MATCHES]                                           ]8;id=783093;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=974276;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

[04/26/24 10:34:14] INFO     query execution done                                                     ]8;id=362208;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=105054;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 0                                      ]8;id=638660;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=105630;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [22]:
df_matches.shape

(5168, 16)

In [23]:
# df_matches = df_matches[df_matches['SEASON'] == 2324]

In [24]:
matches_to_scarpe = set(fbref_schedule['game_id']) - set(df_matches['MATCH_ID'])
matches_to_scarpe = list(matches_to_scarpe)

In [30]:
len(matches_to_scarpe)

11

In [28]:
matches_to_scarpe.append('3435dfcc')

In [27]:
# matches_to_scarpe = list(fbref_schedule['game_id'])

In [28]:
# ## Create empty dataframe with 
# pd.DataFrame(columns=['jersey_number', 'player', 'team', 'is_starter', 'position', 'minutes_played'], index=['league', 'season',
#                                                                                                               'game'])

In [27]:
failed_match_ids = []

In [31]:
for i, val in tqdm(enumerate(matches_to_scarpe)):
    if i == 0:
        fbref_lineups = fbref.read_lineup(match_id=val)
    else:
        try:
            fbref_lineups = pd.concat([fbref_lineups, fbref.read_lineup(match_id=val)])
        except:
            failed_match_ids.append(val)

0it [00:00, ?it/s]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 10:36:23] INFO     [1/1] Retrieving game with id=ee21eba2                                    ]8;id=928591;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=363792;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#884\884]8;;\

1it [00:55, 55.77s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 10:37:18] INFO     [1/1] Retrieving game with id=971e0a29                                    ]8;id=780320;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=555540;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#884\884]8;;\

2it [01:51, 55.89s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


...

9it [08:08, 53.52s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 10:44:30] INFO     [1/1] Retrieving game with id=2e209def                                    ]8;id=447002;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=720025;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#884\884]8;;\

10it [09:02, 53.84s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 10:45:25] INFO     [1/1] Retrieving game with id=3435dfcc                                    ]8;id=626775;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=20928;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#884\884]8;;\

11it [09:57, 54.30s/it]


In [32]:
fbref_lineups.to_csv('fbref_lineups_hold.csv')
# fbref_lineups = pd.read_csv('fbref_lineups_hold.csv')

In [33]:
# fbref_lineups.set_index(['league', 'season', 'game'], inplace=True)

In [34]:
failed_match_ids

[nan]

In [35]:
fbref_lineups.loc[fbref_lineups['team'] == 'Brighton & Hove Albion', 'team'] = 'Brighton'
fbref_lineups.loc[fbref_lineups['team'] == 'Manchester United', 'team'] = 'Manchester Utd'
fbref_lineups.loc[fbref_lineups['team'] == 'Newcastle United', 'team'] = 'Newcastle Utd'
fbref_lineups.loc[fbref_lineups['team'] == 'Nottingham Forest', 'team'] = "Nott'ham Forest"
fbref_lineups.loc[fbref_lineups['team'] == 'Sheffield United', 'team'] = "Sheffield Utd"
fbref_lineups.loc[fbref_lineups['team'] == 'Tottenham Hotspur', 'team'] = 'Tottenham'
fbref_lineups.loc[fbref_lineups['team'] == 'West Ham United', 'team'] = 'West Ham'
fbref_lineups.loc[fbref_lineups['team'] == 'Wolverhampton Wanderers', 'team'] = 'Wolves'

In [36]:
fbref_lineups.replace({"Jarrell Quansah": "Jarell Quansah"}, inplace=True)
fbref_lineups.replace({"Omotayo Adaramola": "Tayo Adaramola"}, inplace=True)
fbref_lineups.replace({"Cristóbal Montiel": "Luis Montiel"}, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\2954072205.py:1: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  fbref_lineups.replace({"Jarrell Quansah": "Jarell Quansah"}, inplace=True)


In [37]:
# fbref_lineups.reset_index(inplace=True)
# fbref_lineups.loc[fbref_lineups['team'] == 'Real Betis', 'team'] = 'Betis'
# fbref_lineups.set_index(['league', 'season', 'game'], inplace=True)

In [38]:
fbref_team_standard = fbref_team_standard.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
# fbref_team_standard_oppo = fbref_team_standard_oppo.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_shooting = fbref_team_shooting.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_shooting_oppo = fbref_team_shooting_oppo.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_passing = fbref_team_passing.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_passing_oppo = fbref_team_passing_oppo.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_defense = fbref_team_defense.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_possession = fbref_team_possession.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_team_misc = fbref_team_misc.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_keeper = fbref_keeper.rename_axis(index={'team': 'TEAM_NAME', 'season': 'SEASON', 'league': 'COMPETITION'})
fbref_schedule = fbref_schedule.rename_axis(index={'season': 'SEASON', 'league': 'COMPETITION'})
fbref_lineups = fbref_lineups.rename_axis(index={'season': 'SEASON', 'league': 'COMPETITION'})
fbref_lineups.rename({'team': 'TEAM_NAME'}, axis=1, inplace=True)
# fbref_lineups.rename({'season': 'SEASON'}, axis=1, inplace=True)

In [39]:
fbref_team_standard

players_used   Age  Poss Playing Time  \
                                                                         MP   
COMPETITION        SEASON TEAM_NAME                                           
ENG-Premier League 2324   Arsenal               25  25.7  58.9           34   
                          Aston Villa           30  27.6  54.5           34   
                          Bournemouth           29  26.5  44.8           34   
                          Brentford             28  27.4  44.2           34   
                          Brighton              30  26.7  60.5           33   
...                                            ...   ...   ...          ...   
ITA-Serie A        2324   Roma                  30  28.7  54.9           33   
                          Salernitana           36  28.2  44.7           33   
                          Sassuolo              30  27.2  44.9           33   
                          Torino                28  27.2  52.2           33   
                          Udinese               32  26.6  39.5           33   

                                                       Performance           \
                                      Starts   Min 90s         Gls Ast  G+A   
COMPETITION        SEASON TEAM_NAME                                           
ENG-Premier League 2324   Arsenal        374  3060  34          78  55  133   
                          Aston Villa    374  3060  34          68  51  119   
                          Bournemouth    374  3060  34          48  35   83   
                          Brentford      374  3060  34          50  34   84   
                          Brighton       363  2970  33          47  35   82   
...                                      ...   ...  ..         ...  ..  ...   
ITA-Serie A        2324   Roma           363  2970  33          58  40   98   
                          Salernitana    363  2970  33          26  22   48   
                          Sassuolo       363  2970  33          38  26   64   
                          Torino         363  2970  33          30  24   54   
                          Udinese        363  2970  33          30  20   50   

                                                              Expected        \
                                      G-PK PK PKatt CrdY CrdR       xG  npxG   
COMPETITION        SEASON TEAM_NAME                                            
ENG-Premier League 2324   Arsenal       69  9     9   55    2     67.4  60.5   
                          Aston Villa   64  4     4   85    2     58.2  55.1   
                          Bournemouth   46  2     3   69    3     50.7  48.3   
                          Brentford     47  3     3   80    2     54.5  52.4   
                          Brighton      42  5     5   79    3     48.9  45.3   
...                                    ... ..   ...  ...  ...      ...   ...   
ITA-Serie A        2324   Roma          49  9    10   89    2     44.8  37.3   
                          Salernitana   24  2     2   79    3     25.4  23.8   
                          Sassuolo      32  6     7   61    3     36.2  31.0   
                          Torino        28  2     2   69    1     34.1  32.5   
                          Udinese       28  2     3   83    5     34.3  32.3   

                                                     Progression        \
                                        xAG npxG+xAG        PrgC  PrgP   
COMPETITION        SEASON TEAM_NAME                                      
ENG-Premier League 2324   Arsenal      48.1    108.6         752  1905   
                          Aston Villa  43.8     98.9         718  1368   
                          Bournemouth  36.4     84.7         642  1199   
                          Brentford    39.5     91.9         434  1144   
                          Brighton     35.8     81.1         745  1596   
...                                     ...      ...         ...   ...   
ITA-Serie A        2324   Roma       

In [40]:
## Get rid of incomplete games (Thank God Tom Lockyear is good <3)
fbref_schedule = fbref_schedule.dropna(subset=['home_xg'])

## Get rid of 'vs ' in the TEAM_NAME column
fbref_team_passing_oppo.reset_index(inplace=True)
fbref_team_shooting_oppo.reset_index(inplace=True)

In [41]:
fbref_schedule = fbref_schedule.dropna(subset=['week'])

In [42]:
fbref_team_passing_oppo['TEAM_NAME'] = fbref_team_passing_oppo['TEAM_NAME'].str.replace('vs ', '')
fbref_team_shooting_oppo['TEAM_NAME'] = fbref_team_shooting_oppo['TEAM_NAME'].str.replace('vs ', '')

fbref_team_passing_oppo.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)
fbref_team_shooting_oppo.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [43]:
def make_season_integer(df):
    indexes = df.index.names
    df = df.reset_index()
    df['SEASON'] = df['SEASON'].astype(int)
    df = df.set_index(indexes)
    return df

fbref_team_standard = make_season_integer(fbref_team_standard)
# fbref_team_standard_oppo = make_season_integer(fbref_team_standard_oppo)
fbref_team_shooting = make_season_integer(fbref_team_shooting)
fbref_team_shooting_oppo = make_season_integer(fbref_team_shooting_oppo)
fbref_team_passing = make_season_integer(fbref_team_passing)
fbref_team_passing_oppo = make_season_integer(fbref_team_passing_oppo)
fbref_team_defense = make_season_integer(fbref_team_defense)
fbref_team_possession = make_season_integer(fbref_team_possession)
fbref_team_misc = make_season_integer(fbref_team_misc)
fbref_schedule = make_season_integer(fbref_schedule)
fbref_keeper = make_season_integer(fbref_keeper)
fbref_lineups = make_season_integer(fbref_lineups)

In [44]:
def name_corrector(df):
    indexes = df.index.names
    df = df.reset_index()
    # df['SEASON'] = df['SEASON'].astype(int)
    df.loc[df['TEAM_NAME'] == 'Milan', 'TEAM_NAME'] = 'AC Milan'
    df = df.set_index(indexes)
    return df

fbref_team_standard = name_corrector(fbref_team_standard)
# fbref_team_standard_oppo = name_corrector(fbref_team_standard_oppo)
fbref_team_shooting = name_corrector(fbref_team_shooting)
fbref_team_shooting_oppo = name_corrector(fbref_team_shooting_oppo)
fbref_team_passing = name_corrector(fbref_team_passing)
fbref_team_passing_oppo = name_corrector(fbref_team_passing_oppo)
fbref_team_defense = name_corrector(fbref_team_defense)
fbref_team_possession = name_corrector(fbref_team_possession)
fbref_team_misc = name_corrector(fbref_team_misc)
# fbref_schedule = name_corrector(fbref_schedule)
fbref_keeper = name_corrector(fbref_keeper)

In [45]:
team_matches_played = fbref_team_standard['Playing Time'].MP
team_goals_scored = understat_table.G
team_npxG_90 = fbref_team_standard['Per 90 Minutes'].npxG
team_goals_conceded = understat_table.GA
# team_xG_against_90 = fbref_team_standard_oppo['Per 90 Minutes'].xG
team_shots = fbref_team_shooting['Standard'].Sh
team_shotsOT = fbref_team_shooting['Standard'].SoT
team_pass_completed = fbref_team_passing["Total"].Cmp
team_pass_attempted = fbref_team_passing["Total"].Att
team_tackles = fbref_team_defense.Tackles.Tkl
team_tackles_won = fbref_team_defense.Tackles.TklW
team_takeons_attempted = fbref_team_possession['Take-Ons'].Att
team_takeons_completed = fbref_team_possession['Take-Ons'].Succ
team_crossesintoPA = fbref_team_passing['CrsPA']
team_fouls_against = fbref_team_misc['Performance']['Fld']
team_fouls_made = fbref_team_misc['Performance']['Fls']
team_interceptions = fbref_team_defense['Int']
team_blocks_shots = fbref_team_defense['Blocks'].Sh
team_blocks_pass = fbref_team_defense['Blocks'].Pass
team_clearances = fbref_team_defense.Clr
team_aerials_won = fbref_team_misc['Aerial Duels'].Won
team_aerials_lost = fbref_team_misc['Aerial Duels'].Lost
team_shots_faced = fbref_team_shooting_oppo['Standard'].Sh

In [46]:
team_recoveries= fbref_team_misc['Performance']['Recov']

In [47]:
teams_poss_won = team_interceptions + team_tackles_won + team_recoveries + team_blocks_shots + \
    team_blocks_pass + team_aerials_won
team_OPPDA = understat_table['OPPDA']
team_final_3rd_passes_against =  fbref_team_passing_oppo['1/3']
team_cleansheets = fbref_keeper['Performance']['CS']

In [48]:
team_names = fbref_team_standard.reset_index()[['TEAM_NAME','url']]
team_names['TEAM_FBREF_ID'] = team_names['url'].apply(lambda x: x.split('/')[3])      ## Extracting team_id from URL
team_names.drop(columns=['url'], inplace=True)
team_names.columns = team_names.columns.droplevel(1)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\2026419047.py:3: PerformanceWarning: dropping on a non-lexsorted multi-index without a level parameter may impact performance.
  team_names.drop(columns=['url'], inplace=True)


In [49]:
team_names['TEAM_FBREF_ID'] = team_names['TEAM_FBREF_ID'].astype('string')

In [50]:
team_names.drop_duplicates(inplace=True)

## WhoScored Data

In [51]:
ws = sd.WhoScored(leagues=['ENG-Premier League', 'GER-Bundesliga', "ESP-La Liga", 'ITA-Serie A', 'FRA-Ligue 1'], 
                  seasons=["2324"])
# ws = sd.WhoScored(leagues=['FRA-Ligue 1'], seasons=["2324"])

[04/26/24 11:06:33] INFO     Saving cached data to C:\Users\ksbha\soccerdata\data\WhoScored           ]8;id=601916;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py\_common.py]8;;\:]8;id=405636;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\_common.py#92\92]8;;\

[04/26/24 11:06:34] INFO     patching driver executable                                              ]8;id=218336;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\undetected_chromedriver\patcher.py\patcher.py]8;;\:]8;id=714036;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\undetected_chromedriver\patcher.py#346\346]8;;\
                             C:\Users\ksbha\appdata\roaming\undetected_chromedriver\undetected_chrom               
                             edriver.exe                                                                           

In [52]:
ws_schedule = ws.read_schedule()

[04/26/24 11:07:36] INFO     Scraping game schedule from                                           ]8;id=172000;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=899292;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#428\428]8;;\
                             https://www.whoscored.com/Regions/252/Tournaments/2/Seasons/9618/Engl                 
                             and-Premier-League                                                                    

                    INFO     Scraping game schedule for Tuesday, Apr 2 2024                        ]8;id=929149;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=878497;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

[04/26/24 11:07:37] INFO     Scraping game schedule for Wednesday, Apr 3 2024                      ]8;id=811422;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=390065;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

                    INFO     Scraping game schedule for Thursday, Apr 4 2024                       ]8;id=800281;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=338843;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

                    INFO     Scraping game schedule for Saturday, Apr 6 2024                       ]8;id=397574;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=169921;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

...

                    INFO     Scraping game schedule for Saturday, Aug 19 2023                      ]8;id=468997;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=436457;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

[04/26/24 11:14:09] INFO     Scraping game schedule for Sunday, Aug 20 2023                        ]8;id=663643;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=45561;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

                    INFO     Scraping game schedule for Friday, Aug 25 2023                        ]8;id=605296;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=374423;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

                    INFO     Scraping game schedule for Saturday, Aug 26 2023                      ]8;id=808543;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=485648;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

                    INFO     Scraping game schedule for Sunday, Aug 27 2023                        ]8;id=860512;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=488559;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

In [52]:
# ws_schedule = pd.read_csv('ws_schedule.csv')

In [53]:
ws_schedule.to_csv('ws_schedule.csv')

In [54]:
ws_schedule = ws_schedule[ws_schedule['date'] < datetime.datetime.now().strftime('%Y-%m-%d')]

In [55]:
fbref_schedule = fbref_schedule.dropna(subset=['home_xg'])

In [56]:
ws_schedule = ws_schedule.reset_index().rename({'league':"COMPETITION", "season":"SEASON"}, axis=1)
ws_schedule.set_index(['COMPETITION', 'SEASON', 'game'], inplace=True)

In [57]:
ws_schedule.loc[ws_schedule['home_team'] == 'Manchester United', 'home_team'] = 'Manchester Utd'
ws_schedule.loc[ws_schedule['away_team'] == 'Manchester United', 'away_team'] = 'Manchester Utd'
ws_schedule.loc[ws_schedule['home_team'] == 'Newcastle United', 'home_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['away_team'] == 'Newcastle United', 'away_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['home_team'] == 'Newcastle', 'home_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['away_team'] == 'Newcastle', 'away_team'] = 'Newcastle Utd'
ws_schedule.loc[ws_schedule['home_team'] == 'Tottenham Hotspur', 'home_team'] = 'Tottenham'
ws_schedule.loc[ws_schedule['away_team'] == 'Tottenham Hotspur', 'away_team'] = 'Tottenham'
ws_schedule.loc[ws_schedule['home_team'] == 'Wolverhampton Wanderers', 'home_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['away_team'] == 'Wolverhampton Wanderers', 'away_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['home_team'] == 'Wolverhampton', 'home_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['away_team'] == 'Wolverhampton', 'away_team'] = 'Wolves'
ws_schedule.loc[ws_schedule['home_team'] == 'Nottingham Forest', 'home_team'] = "Nott'ham Forest"
ws_schedule.loc[ws_schedule['away_team'] == 'Nottingham Forest', 'away_team'] = "Nott'ham Forest"
ws_schedule.loc[ws_schedule['home_team'] == 'Leicester', 'home_team'] = "Leicester City"
ws_schedule.loc[ws_schedule['away_team'] == 'Leicester', 'away_team'] = "Leicester City"
ws_schedule.loc[ws_schedule['home_team'] == 'Leeds', 'home_team'] = "Leeds United"
ws_schedule.loc[ws_schedule['away_team'] == 'Leeds', 'away_team'] = "Leeds United"
ws_schedule.loc[ws_schedule['home_team'] == 'Sheffield United', 'home_team'] = "Sheffield Utd"
ws_schedule.loc[ws_schedule['away_team'] == 'Sheffield United', 'away_team'] = "Sheffield Utd"
ws_schedule.loc[ws_schedule['home_team'] == 'Luton', 'home_team'] = "Luton Town"
ws_schedule.loc[ws_schedule['away_team'] == 'Luton', 'away_team'] = "Luton Town"
ws_schedule.loc[ws_schedule['home_team'] == 'Norwich', 'home_team'] = "Norwich City"
ws_schedule.loc[ws_schedule['away_team'] == 'Norwich', 'away_team'] = "Norwich City"

ws_schedule.loc[ws_schedule['home_team'] == 'Atletico Madrid', 'home_team'] = 'Atlético Madrid'
ws_schedule.loc[ws_schedule['away_team'] == 'Atletico Madrid', 'away_team'] = 'Atlético Madrid'
ws_schedule.loc[ws_schedule['home_team'] == 'Cadiz', 'home_team'] = 'Cádiz'
ws_schedule.loc[ws_schedule['away_team'] == 'Cadiz', 'away_team'] = 'Cádiz'
ws_schedule.loc[ws_schedule['home_team'] == 'Deportivo Alaves', 'home_team'] = 'Alavés'
ws_schedule.loc[ws_schedule['away_team'] == 'Deportivo Alaves', 'away_team'] = 'Alavés'
ws_schedule.loc[ws_schedule['home_team'] == 'Real Betis', 'home_team'] = 'Betis'
ws_schedule.loc[ws_schedule['away_team'] == 'Real Betis', 'away_team'] = 'Betis'
ws_schedule.loc[ws_schedule['home_team'] == 'Deportivo Alaves', 'home_team'] = 'Alavés'
ws_schedule.loc[ws_schedule['away_team'] == 'Deportivo Alaves', 'away_team'] = 'Alavés'
ws_schedule.loc[ws_schedule['home_team'] == 'Real Valladolid', 'home_team'] = 'Valladolid'
ws_schedule.loc[ws_schedule['away_team'] == 'Real Valladolid', 'away_team'] = 'Valladolid'
ws_schedule.loc[ws_schedule['home_team'] == 'Almeria', 'home_team'] = 'Almería'
ws_schedule.loc[ws_schedule['away_team'] == 'Almeria', 'away_team'] = 'Almería'

ws_schedule.loc[ws_schedule['home_team'] == 'Arminia Bielefeld', 'home_team'] = 'Arminia'
ws_schedule.loc[ws_schedule['away_team'] == 'Arminia Bielefeld', 'away_team'] = 'Arminia'
ws_schedule.loc[ws_schedule['home_team'] == 'Bayer Leverkusen', 'home_team'] = 'Leverkusen'
ws_schedule.loc[ws_schedule['away_team'] == 'Bayer Leverkusen', 'away_team'] = 'Leverkusen'
ws_schedule.loc[ws_schedule['home_team'] == 'Borussia Dortmund', 'home_team'] = 'Dortmund'
ws_schedule.loc[ws_schedule['away_team'] == 'Borussia Dortmund', 'away_team'] = 'Dortmund'
ws_schedule.loc[ws_schedule['home_team'] == 'Borussia M.Gladbach', 'home_team'] = "M'Gladbach"
ws_schedule.loc[ws_schedule['away_team'] == 'Borussia M.Gladbach', 'away_team'] = "M'Gladbach"
ws_schedule.loc[ws_schedule['home_team'] == 'Eintracht Frankfurt', 'home_team'] = "Eint Frankfurt"
ws_schedule.loc[ws_schedule['away_team'] == 'Eintracht Frankfurt', 'away_team'] = "Eint Frankfurt"
ws_schedule.loc[ws_schedule['home_team'] == 'Greuther Fuerth', 'home_team'] = "Greuther Fürth"
ws_schedule.loc[ws_schedule['away_team'] == 'Greuther Fuerth', 'away_team'] = "Greuther Fürth"
ws_schedule.loc[ws_schedule['home_team'] == 'FC Koln', 'home_team'] = "Köln"
ws_schedule.loc[ws_schedule['away_team'] == 'FC Koln', 'away_team'] = "Köln"
ws_schedule.loc[ws_schedule['home_team'] == 'Hertha Berlin', 'home_team'] = "Hertha BSC"
ws_schedule.loc[ws_schedule['away_team'] == 'Hertha Berlin', 'away_team'] = "Hertha BSC"
ws_schedule.loc[ws_schedule['home_team'] == 'VfB Stuttgart', 'home_team'] = "Stuttgart"
ws_schedule.loc[ws_schedule['away_team'] == 'VfB Stuttgart', 'away_team'] = "Stuttgart"
ws_schedule.loc[ws_schedule['home_team'] == 'Darmstadt', 'home_team'] = "Darmstadt 98"
ws_schedule.loc[ws_schedule['away_team'] == 'Darmstadt', 'away_team'] = "Darmstadt 98"
ws_schedule.loc[ws_schedule['home_team'] == 'FC Heidenheim', 'home_team'] = "Heidenheim"
ws_schedule.loc[ws_schedule['away_team'] == 'FC Heidenheim', 'away_team'] = "Heidenheim"

ws_schedule.loc[ws_schedule['home_team'] == 'Verona', 'home_team'] = "Hellas Verona"
ws_schedule.loc[ws_schedule['away_team'] == 'Verona', 'away_team'] = "Hellas Verona"

ws_schedule.loc[ws_schedule['home_team'] == 'Paris Saint-Germain', 'home_team'] = "Paris S-G"
ws_schedule.loc[ws_schedule['away_team'] == 'Paris Saint-Germain', 'away_team'] = "Paris S-G"
ws_schedule.loc[ws_schedule['home_team'] == 'AC Ajaccio', 'home_team'] = "Ajaccio"
ws_schedule.loc[ws_schedule['away_team'] == 'AC Ajaccio', 'away_team'] = "Ajaccio"
ws_schedule.loc[ws_schedule['home_team'] == 'Saint-Etienne', 'home_team'] = "Saint-Étienne"
ws_schedule.loc[ws_schedule['away_team'] == 'Saint-Etienne', 'away_team'] = "Saint-Étienne"

In [58]:
fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Bayer Leverkusen', 'TEAM_NAME'] = 'Leverkusen'
fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Eintracht Frankfurt', 'TEAM_NAME'] = 'Eint Frankfurt'
fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Mönchengladbach', 'TEAM_NAME'] = "M'Gladbach"
fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Milan', 'TEAM_NAME'] = "AC Milan"
fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Internazionale', 'TEAM_NAME'] = "Inter"
fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Paris Saint-Germain', 'TEAM_NAME'] = "Paris S-G"
fbref_lineups.loc[fbref_lineups['TEAM_NAME'] == 'Real Betis', 'TEAM_NAME'] = "Betis"

In [59]:
ws_schedule.reset_index(inplace=True)
fbref_schedule.reset_index(inplace=True)

In [60]:
ws_schedule = ws_schedule.rename({'game_id':"ws_game_id"}, axis=1)

In [61]:
ws_schedule['SEASON'] = ws_schedule['SEASON'].astype('int64')

In [62]:
sorted(fbref_schedule['home_team'].unique())==sorted(ws_schedule['home_team'].unique())

True

In [63]:
fbref_schedule = pd.merge(fbref_schedule, ws_schedule[["COMPETITION", "SEASON", "home_team", "away_team","ws_game_id"]], 
          on=["COMPETITION", "SEASON", "home_team", "away_team"], how='inner')

In [64]:
loader = ws.read_events(output_fmt='loader')

[04/26/24 11:18:04] INFO     Scraping game schedule from                                           ]8;id=965126;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=312139;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#428\428]8;;\
                             https://www.whoscored.com/Regions/252/Tournaments/2/Seasons/9618/Engl                 
                             and-Premier-League                                                                    

                    INFO     Scraping game schedule for Tuesday, Apr 2 2024                        ]8;id=38726;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=228722;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

[04/26/24 11:18:05] INFO     Scraping game schedule for Wednesday, Apr 3 2024                      ]8;id=263118;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=859657;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

[04/26/24 11:18:06] INFO     Scraping game schedule for Thursday, Apr 4 2024                       ]8;id=993193;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=605942;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

                    INFO     Scraping game schedule for Saturday, Apr 6 2024                       ]8;id=447816;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=239997;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

...

                    INFO     [1570/1574] Retrieving game with id=1729356                           ]8;id=749883;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=829597;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#694\694]8;;\

                    INFO     [1571/1574] Retrieving game with id=1734798                           ]8;id=295113;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=505426;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#694\694]8;;\

                    INFO     [1572/1574] Retrieving game with id=1729407                           ]8;id=669817;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=787225;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#694\694]8;;\

                    INFO     [1573/1574] Retrieving game with id=1746066                           ]8;id=787129;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=40658;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#694\694]8;;\

                    INFO     [1574/1574] Retrieving game with id=1734658                           ]8;id=124866;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=449668;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#694\694]8;;\

In [65]:
print("help")

help


In [66]:
game_ids = fbref_schedule[fbref_schedule['game_id'].isin(matches_to_scarpe)]['ws_game_id'].unique()

In [67]:
ws_players = pd.DataFrame(columns=['game_id', 'team_id', 'player_id', 'player_name', 
                                   'is_starter','minutes_played', 'jersey_number', 'starting_position'])

In [68]:
ws_teams=pd.DataFrame(columns=['team_id', 'team_name'])

In [69]:
games_no_players = []

In [70]:
# game_ids = fbref_schedule['ws_game_id'].unique()
# matches_to_scarpe = fbref_schedule['game_id'].unique()

In [71]:
len(matches_to_scarpe)

11

In [72]:
game_ids

array([1729409, 1729418, 1729421, 1729429, 1729435, 1729412, 1741294,
       1741293, 1741296, 1746369], dtype=int64)

In [73]:
for game in tqdm(game_ids):
    try:
        ws_teams = pd.concat([ws_teams, loader.teams(game_id=game)])
        ws_players = pd.concat([ws_players, loader.players(game_id=game)])
    except:
        games_no_players.append(game)

100%|██████████| 10/10 [00:02<00:00,  3.92it/s]


In [74]:
ws_teams.drop_duplicates(inplace=True)

In [75]:
ws_teams.reset_index(drop=True, inplace=True)

In [76]:
sorted(ws_schedule['home_team'].unique()) == sorted(ws_teams['team_name'])

False

In [77]:
len(sorted(ws_schedule['home_team'].unique()))

96

In [78]:
len(sorted(ws_teams['team_name']))

20

In [79]:
ws_teams.loc[ws_teams['team_name'] == 'Arminia Bielefeld', 'team_name'] = 'Arminia'
ws_teams.loc[ws_teams['team_name'] == 'Bayern', 'team_name'] = 'Bayern Munich'
ws_teams.loc[ws_teams['team_name'] == 'Borussia Dortmund', 'team_name'] = 'Dortmund'
ws_teams.loc[ws_teams['team_name'] == 'Borussia M.Gladbach', 'team_name'] = "M'Gladbach"
ws_teams.loc[ws_teams['team_name'] == 'Eintracht Frankfurt', 'team_name'] = "Eint Frankfurt"
ws_teams.loc[ws_teams['team_name'] == 'FC Koln', 'team_name'] = 'Köln'
ws_teams.loc[ws_teams['team_name'] == 'Mainz', 'team_name'] = "Mainz 05"
ws_teams.loc[ws_teams['team_name'] == 'RBL', 'team_name'] = "RB Leipzig"
ws_teams.loc[ws_teams['team_name'] == 'Greuther Fuerth', 'team_name'] = "Greuther Fürth"
ws_teams.loc[ws_teams['team_name'] == 'Hertha Berlin', 'team_name'] = "Hertha BSC"
ws_teams.loc[ws_teams['team_name'] == 'Schalke', 'team_name'] = 'Schalke 04'
ws_teams.loc[ws_teams['team_name'] == 'Darmstadt', 'team_name'] = "Darmstadt 98"
ws_teams.loc[ws_teams['team_name'] == 'FC Heidenheim', 'team_name'] = 'Heidenheim'

ws_teams.loc[ws_teams['team_name'] == 'Luton', 'team_name'] = 'Luton Town'
ws_teams.loc[ws_teams['team_name'] == 'Nottingham Forest', 'team_name'] = "Nott'ham Forest"
ws_teams.loc[ws_teams['team_name'] == 'Sheff Utd', 'team_name'] = "Sheffield Utd"
ws_teams.loc[ws_teams['team_name'] == 'Man Utd', 'team_name'] = "Manchester Utd"
ws_teams.loc[ws_teams['team_name'] == 'Man City', 'team_name'] = "Manchester City"
ws_teams.loc[ws_teams['team_name'] == 'Newcastle', 'team_name'] = "Newcastle Utd"

ws_teams.loc[ws_teams['team_name'] == 'Atletico', 'team_name'] = 'Atlético Madrid'
ws_teams.loc[ws_teams['team_name'] == 'Cadiz', 'team_name'] = 'Cádiz'
ws_teams.loc[ws_teams['team_name'] == 'Deportivo Alaves', 'team_name'] = 'Alavés'
ws_teams.loc[ws_teams['team_name'] == 'Real Betis', 'team_name'] = 'Betis'
ws_teams.loc[ws_teams['team_name'] == 'Almeria', 'team_name'] = 'Almería'
ws_teams.loc[ws_teams['team_name'] == 'Real Valladolid', 'team_name'] = 'Valladolid'

ws_teams.loc[ws_teams['team_name'] == 'Verona', 'team_name'] = 'Hellas Verona'

ws_teams.loc[ws_teams['team_name'] == 'PSG', 'team_name'] = 'Paris S-G'
ws_teams.loc[ws_teams['team_name'] == 'Saint-Etienne', 'team_name'] = 'Saint-Étienne'
ws_teams.loc[ws_teams['team_name'] == 'AC Ajaccio', 'team_name'] = "Ajaccio"

In [80]:
# WhoScored decide to name Willy Boly with two different names. Idiots
ws_players.replace({"Willy-Arnaud Boly": "Willy Boly"}, inplace=True)
ws_players.replace({"Kepa": "Kepa Arrizabalaga"}, inplace=True)
ws_players.replace({"Yehor Yarmolyuk": "Yehor Yarmoliuk"}, inplace=True)
ws_players.replace({"Vitalii Mykolenko": "Vitaliy Mykolenko"}, inplace=True)
ws_players.replace({"Dan Bentley": "Daniel Bentley"}, inplace=True)
ws_players.replace({"Toti": "Toti Gomes"}, inplace=True)
ws_players.replace({"Joe Hodge": "Joseph Hodge"}, inplace=True)
ws_players.replace({"Jonny Otto": "Jonny"}, inplace=True)
ws_players.replace({"Álvaro Carreras": "Álvaro Fernández"}, inplace=True)
ws_players.replace({"Alisson Becker": "Alisson"}, inplace=True)
ws_players.replace({"Andy Robertson": "Andrew Robertson"}, inplace=True)
ws_players.replace({"Konstantinos Tsimikas": "Kostas Tsimikas"}, inplace=True)
ws_players.replace({"Alphonse Aréola": "Alphonse Areola"}, inplace=True)
ws_players.replace({"Pape Sarr": "Pape Matar Sarr"}, inplace=True)
ws_players.replace({"Yago Alonso": "Yago Santiago"}, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\743149616.py:2: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  ws_players.replace({"Willy-Arnaud Boly": "Willy Boly"}, inplace=True)


## Snowflake Data Upload

In [81]:
SNOWFLAKE_USER = 'karan14'
SNOWFLAKE_PASSWORD = 'Snowfl@key0014'
SNOWFLAKE_ACCOUNT = 'lv65293.ca-central-1.aws'
SNOWFLAKE_WAREHOUSE = 'COMPUTE_WH'
SNOWFLAKE_DATABASE = 'GEGENSTATS'
SNOWFLAKE_SCHEMA = 'TABLES'

In [82]:
conn = snowflake.connector.connect(
    user=SNOWFLAKE_USER,
    password=SNOWFLAKE_PASSWORD,
    account=SNOWFLAKE_ACCOUNT,
    warehouse=SNOWFLAKE_WAREHOUSE,
    database=SNOWFLAKE_DATABASE,
    schema=SNOWFLAKE_SCHEMA
    )

[04/26/24 11:50:19] INFO     Snowflake Connector for Python Version: 3.3.1, Python Version:       ]8;id=121842;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=779016;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#334\334]8;;\
                             3.11.5, Platform: Windows-10-10.0.22000-SP0                                           

                    INFO     This connection is in OCSP Fail Open Mode. TLS Certificates would   ]8;id=466661;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py\connection.py]8;;\:]8;id=110033;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\connection.py#1103\1103]8;;\
                             be checked for validity and revocation status. Any other                              
                             Certificate Revocation related exceptions or OCSP Responder                           
                             failures would be disregarded in favor of connectivity.                               

In [83]:
cur = conn.cursor()
cur.execute(f"USE WAREHOUSE {SNOWFLAKE_WAREHOUSE}")

[04/26/24 11:50:21] INFO     query: [USE WAREHOUSE COMPUTE_WH]                                        ]8;id=160965;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=393838;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=779311;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=551653;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=939107;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=282775;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [84]:
create_schema_sql = f"CREATE SCHEMA IF NOT EXISTS {SNOWFLAKE_SCHEMA}"
cur.execute(create_schema_sql)

                    INFO     query: [CREATE SCHEMA IF NOT EXISTS TABLES]                              ]8;id=101780;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=268062;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=89710;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=720090;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=276548;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=524632;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [85]:
print("The Snowflake warehouse being used is:", SNOWFLAKE_WAREHOUSE)

The Snowflake warehouse being used is: COMPUTE_WH


In [86]:
cur.execute('SELECT * FROM TEAMS')
team_rows = cur.fetchall()
column_names = [desc[0] for desc in cur.description]
curr_team_names = pd.DataFrame(team_rows, columns=column_names)

[04/26/24 11:50:24] INFO     query: [SELECT * FROM TEAMS]                                             ]8;id=160722;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=556219;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=759676;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=317184;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 119                                    ]8;id=721886;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=969005;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [87]:
## Below (if not blank) are the teams you need to create LOGOS for
team_names_not_in_curr = team_names[~team_names['TEAM_NAME'].isin(curr_team_names['TEAM_NAME'])]
team_names_not_in_curr

Empty DataFrame
Columns: [TEAM_NAME, TEAM_FBREF_ID]
Index: []

In [88]:
def upsert_to_snowflake(table_name, dataframe, primary_keys):
    if isinstance(primary_keys, str):
        primary_keys = [primary_keys]

    temp_table_name = f"{table_name}_TEMP"
    success, nchunks, nrows, _ = write_pandas(conn, dataframe, temp_table_name, auto_create_table=True)

    on_condition = ' AND '.join([f"{table_name}.{pk} = {temp_table_name}.{pk}" for pk in primary_keys])

    update_columns = [col for col in dataframe.columns if col not in primary_keys]
    update_sql = ', '.join([f"{table_name}.{col} = {temp_table_name}.{col}" for col in update_columns])

    merge_sql = f"""
    MERGE INTO {table_name} USING {temp_table_name}
    ON {on_condition}
    """

    if update_columns:
        merge_sql += f"""
        WHEN MATCHED THEN
            UPDATE SET
                {update_sql}
        """

    merge_sql += f"""
    WHEN NOT MATCHED THEN
        INSERT ({', '.join(dataframe.columns)})
        VALUES ({', '.join([f"{temp_table_name}.{col}" for col in dataframe.columns])})
    """

    cur.execute(merge_sql)
    cur.execute(f"DROP TABLE IF EXISTS {temp_table_name}")

    print(f"Upsert completed. {nrows} rows processed.")

In [89]:
ws_teams.rename({'team_name':'TEAM_NAME', 'team_id':'TEAM_WS_ID'}, axis=1, inplace=True)

In [90]:
team_logos = \
[["Angers", "https://i.imgur.com/dyRj0Cc.png"], ["Bordeaux", "https://i.imgur.com/2NxcpPo.png"],
 ["Brest", "https://i.imgur.com/klKUp8n.png"], ["Clermont Foot", "https://i.imgur.com/7RHafik.png"],
 ["Lens", "https://i.imgur.com/9hfNDts.png"], ["Lille", "https://i.imgur.com/G3MyVe5.png"],
 ["Lorient", "https://i.imgur.com/9k1Kgp6.png"], ["Lyon", "https://i.imgur.com/F0cNDBC.png"],
 ["Marseille", "https://i.imgur.com/jbim9vo.png"], ["Metz", "https://i.imgur.com/UvYK5II.png"],
 ["Monaco", "https://i.imgur.com/HNfIv5Y.png"], ["Montpellier", "https://i.imgur.com/lwG9vvR.png"],
 ["Nantes", "https://i.imgur.com/rxlejD4.png"], ["Nice", "https://i.imgur.com/bIsadPH.png"],
 ["Paris S-G", "https://i.imgur.com/kuN3QSp.png"], ["Reims", "https://i.imgur.com/xULypbI.png"],
 ["Rennes", "https://i.imgur.com/TZq2Hvr.png"], ["Saint-Étienne", "https://i.imgur.com/iIex5w7.png"],
 ["Strasbourg", "https://i.imgur.com/RKf7LuY.png"], ["Troyes", "https://i.imgur.com/6VTNoyL.png"],
 ["Ajaccio", "https://i.imgur.com/FSm4pRb.png"], ["Auxerre", "https://i.imgur.com/mwlqKAg.png"],
 ["Toulouse", "https://i.imgur.com/dvkjqJ2.png"], ["Le Havre", "https://i.imgur.com/YHGxNQP.png"]
 ]

In [93]:
# team_logos = \
# [["Atalanta", "https://i.imgur.com/SDA0nMH.png"], ["Bologna", "https://i.imgur.com/rVqtfOA.png"],
#  ["Cagliari", "https://i.imgur.com/rbAC6zo.png"], ["Empoli", "https://i.imgur.com/52xSYdX.png"],
#  ["Fiorentina", "https://i.imgur.com/hOQC1jo.png"], ["Genoa", "https://i.imgur.com/KjtIy8U.png"],
#  ["Hellas Verona", "https://i.imgur.com/vhAWZQO.png"], ["Inter", "https://i.imgur.com/JsJ06ke.png"],
#  ["Juventus", "https://i.imgur.com/60XAIJI.png"], ["Lazio", "https://i.imgur.com/SBsGYjm.png"],
#  ["AC Milan", "https://i.imgur.com/1Ze94pt.png"], ["Napoli", "https://i.imgur.com/Ql7LKBZ.png"],
#  ["Roma", "https://i.imgur.com/nhMJAHW.png"], ["Salernitana", "https://i.imgur.com/sYubMBZ.png"],
#  ["Sampdoria", "https://i.imgur.com/MTOvCDt.png"], ["Sassuolo", "https://i.imgur.com/px5mT39.png"],
#  ["Spezia", "https://i.imgur.com/gYVirSf.png"], ["Torino", "https://i.imgur.com/XWmpYeu.png"],
#  ["Udinese", "https://i.imgur.com/Dp0KUmN.png"], ["Venezia", "https://i.imgur.com/VjHBE7d.png"],
#  ["Cremonese", "https://i.imgur.com/r6hDldN.png"], ["Lecce", "https://i.imgur.com/9A4flGu.png"], 
#  ["Monza", "https://i.imgur.com/7bHOIx9.png"], ["Frosinone", "https://i.imgur.com/x8qGMuV.png"]
#  ]

In [94]:
# team_logos = \
# [["Arminia", "https://i.imgur.com/PKcXmoo.png"], ["Augsburg", "https://i.imgur.com/c9rRqYo.png"],
#  ["Bayern Munich", "https://i.imgur.com/rO1xVQh.png"], ["Bochum", "https://i.imgur.com/3LmZ5gX.png"],
#  ["Dortmund", "https://i.imgur.com/DyWKX0s.png"], ["Eint Frankfurt", "https://i.imgur.com/Fz4xh6m.png"],
#  ["Freiburg", "https://i.imgur.com/1JUxe7u.png"], ["Greuther Fürth", "https://i.imgur.com/ttJEUIb.png"],
#  ["Hertha BSC", "https://i.imgur.com/KAgTHoB.png"], ["Hoffenheim", "https://i.imgur.com/dooGO0m.png"],
#  ["Köln", "https://i.imgur.com/Gpz6jl7.png"], ["Leverkusen", "https://i.imgur.com/q3lV6o8.png"],
#  ["M'Gladbach", "https://i.imgur.com/K6aoRqW.png"], ["Mainz 05", "https://i.imgur.com/iOoxKkB.png"],
#  ["RB Leipzig", "https://i.imgur.com/CXfyKw4.png"], ["Stuttgart", "https://i.imgur.com/eQB0wsT.png"],
#  ["Union Berlin", "https://i.imgur.com/e5pjmHx.png"], ["Wolfsburg", "https://i.imgur.com/o2PP4ux.png"],
#  ["Schalke 04", "https://i.imgur.com/FfsE1Kk.png"], ["Werder Bremen", "https://i.imgur.com/XrAnCXM.png"],
#  ["Darmstadt 98", "https://i.imgur.com/CZbwcFI.png"], ["Heidenheim", "https://i.imgur.com/ks2nifY.png"]
#  ]

In [95]:
# team_logos = \
# [["Barcelona", "https://i.imgur.com/1ZRO0Be.png"], ["Villarreal", "https://i.imgur.com/yQJvRBY.png"],
#  ["Valencia", "https://i.imgur.com/Erg2x2b.png"], ["Sevilla", "https://i.imgur.com/z3WXql2.png"],
#  ["Real Sociedad", "https://i.imgur.com/KdMxrGX.png"], ["Real Madrid", "https://i.imgur.com/pPD5ZAg.png"],
#  ["Rayo Vallecano", "https://i.imgur.com/cQ5Mv8I.png"], ["Osasuna", "https://i.imgur.com/6kAlaCy.png"],
#  ["Mallorca", "https://i.imgur.com/Qvdlcxy.png"], ["Levante", "https://i.imgur.com/8fZG4VA.png"],
#  ["Granada", "https://i.imgur.com/ce69kNa.png"], ["Getafe", "https://i.imgur.com/C4eV2p0.png"],
#  ["Espanyol", "https://i.imgur.com/RHTK1eL.png"], ["Elche", "https://i.imgur.com/S9bDHtO.png"],
#  ["Cádiz", "https://i.imgur.com/DztjVQE.png"], ["Celta Vigo", "https://i.imgur.com/kTsF0rV.png"],
#  ["Betis", "https://i.imgur.com/zyGTmAb.png"], ["Atlético Madrid", "https://i.imgur.com/x4c0wbO.png"],
#  ["Athletic Club", "https://i.imgur.com/qI6Uchm.png"], ["Alavés", "https://i.imgur.com/o4rSfuL.png"],
#  ["Almería", "https://i.imgur.com/kFyJaGO.png"], ["Girona", "https://i.imgur.com/0CwKO1D.png"],
#  ["Valladolid", "https://i.imgur.com/HCShRZI.png"], ["Las Palmas", "https://i.imgur.com/KAHlAuF.png"]
#  ]

In [96]:
# team_names = team_names.merge(pd.DataFrame(team_logos, columns=["TEAM_NAME", "TEAM_LOGO_URL"]), on="TEAM_NAME")

In [97]:
# ws_teams.rename({'team_name':'TEAM_NAME', 'team_id':'TEAM_WS_ID'}, axis=1, inplace=True)

In [98]:
# team_names = team_names.merge(ws_teams, on="TEAM_NAME")

In [ ]:
upsert_to_snowflake("TEAMS", team_names, ['TEAM_FBREF_ID'])

In [91]:
team_names = fetch_data(cur, 'SELECT * FROM TEAMS')

[04/26/24 11:50:33] INFO     query: [SELECT * FROM TEAMS]                                             ]8;id=52251;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=337844;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=202548;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=397422;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 119                                    ]8;id=70966;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=758408;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

In [92]:
team_names.drop(columns=['TEAM_LOGO_URL'], inplace=True)

In [93]:
team_standard_stats = understat_table.copy()

In [94]:
# team_standard_stats.reset_index(inplace=True)
# team_standard_stats.loc[team_standard_stats['TEAM_NAME'] == 'Luton', 'TEAM_NAME'] = 'Luton Town'
# team_standard_stats.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [95]:
team_standard_stats['MATCHES_PLAYED'] = team_matches_played

In [96]:
team_standard_stats.reset_index(inplace=True)

In [97]:
team_standard_stats = team_standard_stats.merge(team_names, on='TEAM_NAME', how='left')

In [98]:
team_standard_stats = team_standard_stats[['TEAM_FBREF_ID','SEASON','COMPETITION','MATCHES_PLAYED','TEAM_WINS', 
                                           'TEAM_DRAWS', 'TEAM_LOSSES', 'TEAM_PTS', 'TEAM_XPTS']]

In [99]:
team_standard_stats

TEAM_FBREF_ID  SEASON         COMPETITION  MATCHES_PLAYED TEAM_WINS  \
0       18bb7c10    2324  ENG-Premier League              34        24   
1       8602292d    2324  ENG-Premier League              34        20   
2       4ba7cbea    2324  ENG-Premier League              34        12   
3       cd051869    2324  ENG-Premier League              34         9   
4       d07537b9    2324  ENG-Premier League              33        11   
..           ...     ...                 ...             ...       ...   
91      cf74a709    2324         ITA-Serie A              33        17   
92      c5577084    2324         ITA-Serie A              33         2   
93      e2befd26    2324         ITA-Serie A              33         6   
94      105360fe    2324         ITA-Serie A              33        11   
95      04eea015    2324         ITA-Serie A              33         4   

   TEAM_DRAWS TEAM_LOSSES TEAM_PTS TEAM_XPTS  
0           5           5       77     73.13  
1           6           8       66     52.52  
2           9          13       45      48.8  
3           8          17       35     48.61  
4          11          11       44     46.56  
..        ...         ...      ...       ...  
91          7           9       58      54.5  
92          9          22       15     20.09  
93          8          19       26     35.61  
94         13           9       46     50.35  
95         16          13       28     40.92  

[96 rows x 9 columns]

In [100]:
upsert_to_snowflake("TEAM_STANDARD_STATS", team_standard_stats, ['TEAM_FBREF_ID', 'COMPETITION','SEASON'])

[04/26/24 11:50:41] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=331079;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=923815;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=345291;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=401813;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=412789;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=722906;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=553093;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=469198;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=444024;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=216718;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/26/24 11:50:45] INFO     query execution done                                                     ]8;id=511250;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=941221;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS TEAM_STANDARD_STATS_TEMP]                   ]8;id=562691;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=274465;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=522907;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=364947;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=461024;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=64911;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 96 rows processed.


In [101]:
team_attacking_stats = understat_table.copy()

In [102]:
team_attacking_stats = team_attacking_stats.reset_index().merge(team_names, on='TEAM_NAME', how='left')

In [103]:
team_attacking_stats = team_attacking_stats[['TEAM_NAME','TEAM_FBREF_ID','COMPETITION','SEASON','NPxG','xG']]

In [104]:
team_attacking_stats.rename(columns={'NPxG': 'NPXG', 'xG':'XG'}, inplace=True)

In [105]:
team_attacking_stats.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [106]:
team_attacking_stats['GOALS_SCORED'] = team_goals_scored
team_attacking_stats['SHOTS'] = team_shots
team_attacking_stats['SHOTS_ON_TARGET'] = team_shotsOT
team_attacking_stats['PASS_COMPLETED'] = team_pass_completed
team_attacking_stats['PASS_ATTEMPTED'] = team_pass_attempted
team_attacking_stats['TAKEONS_ATTEMPTED'] = team_takeons_attempted
team_attacking_stats['TAKEONS_COMPLETED'] = team_takeons_completed
team_attacking_stats['CROSSES_INTO_PA'] = team_crossesintoPA
team_attacking_stats['FOULS_AGAINST'] = team_fouls_against

In [107]:
team_attacking_stats.reset_index(inplace=True)
team_attacking_stats.drop(columns=['TEAM_NAME'], inplace=True)

In [108]:
upsert_to_snowflake("TEAM_ATTACKING_STATS", team_attacking_stats, ['TEAM_FBREF_ID', 'COMPETITION','SEASON'])

[04/26/24 11:50:46] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=122728;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=706118;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=77067;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=672279;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=116602;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=243524;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=840864;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=588079;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=291371;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=93501;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

                    INFO     query execution done                                                     ]8;id=367159;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=308847;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

[04/26/24 11:50:49] INFO     query: [DROP TABLE IF EXISTS TEAM_ATTACKING_STATS_TEMP]                  ]8;id=901349;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=264171;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=130367;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=617463;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=702483;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=183859;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 96 rows processed.


In [109]:
team_defending_stats = understat_table.copy()

In [110]:
team_defending_stats = team_defending_stats.reset_index().merge(team_names, on='TEAM_NAME', how='left')

In [111]:
team_defending_stats = team_defending_stats[['TEAM_NAME','TEAM_FBREF_ID','COMPETITION','SEASON']]

In [112]:
team_defending_stats.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [113]:
team_defending_stats['GOALS_CONCEDED'] = team_goals_conceded
team_defending_stats['XG_AGAINST'] = understat_table['XG_AGAINST']
team_defending_stats['NPXG_AGAINST'] = understat_table['NPXG_AGAINST']
team_defending_stats['TACKLES'] = team_tackles
team_defending_stats['TACKLES_WON'] = team_tackles_won
team_defending_stats['FOULS_MADE'] = team_fouls_made
team_defending_stats['INTERCEPTIONS'] = team_interceptions
team_defending_stats['BLOCKED_SHOTS'] = team_blocks_shots
team_defending_stats['BLOCKED_PASSES'] = team_blocks_pass
team_defending_stats['CLEARANCES'] = team_clearances
team_defending_stats['PPDA'] = understat_table['PPDA']
team_defending_stats['OPP_PPDA'] = team_OPPDA
team_defending_stats['POSS_WON'] = teams_poss_won
team_defending_stats['FINAL_3RD_PASSES_AGAINST'] = team_final_3rd_passes_against
team_defending_stats['CLEAN_SHEETS'] = team_cleansheets
team_defending_stats['SHOTS_FACED'] = team_shots_faced

In [114]:
team_defending_stats.reset_index(inplace=True)
team_defending_stats.drop(columns=['TEAM_NAME'], inplace=True)

In [115]:
# sql_command = """
# ALTER TABLE GEGENSTATS.TABLES.TEAM_DEFENDING_STATS 
# ADD COLUMN SHOTS_FACED NUMBER(38,0);
# """

# cur.execute(sql_command)

In [116]:
# team_shots_faced = team_shots_faced.reset_index()

In [117]:
# for index, row in team_shots_faced.iterrows():
#     sql_command = """
#     UPDATE GEGENSTATS.TABLES.TEAM_DEFENDING_STATS
#     SET SHOTS_FACED = %s
#     WHERE TEAM_FBREF_ID = (SELECT TEAM_FBREF_ID FROM GEGENSTATS.TABLES.TEAMS WHERE TEAM_NAME = %s) 
#       AND COMPETITION = %s
#       AND SEASON = %s
#     """

#     values = (row['Sh'], row['TEAM_NAME'], row['COMPETITION'], row['SEASON'])

#     cur.execute(sql_command, values)

In [118]:
upsert_to_snowflake("TEAM_DEFENDING_STATS", team_defending_stats, ['TEAM_FBREF_ID', 'COMPETITION','SEASON'])

[04/26/24 11:50:51] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=652456;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=176756;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=776330;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=651974;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=297927;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=995164;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=848376;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=382422;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=704749;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=849639;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/26/24 11:50:54] INFO     query execution done                                                     ]8;id=715651;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=946825;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS TEAM_DEFENDING_STATS_TEMP]                  ]8;id=414452;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=904585;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=112739;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=580143;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=902639;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=414124;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 96 rows processed.


In [119]:
team_misc_stats = understat_table.copy()

In [120]:
team_misc_stats = team_misc_stats.reset_index().merge(team_names, on='TEAM_NAME', how='left')

In [121]:
team_misc_stats = team_misc_stats[['TEAM_NAME','TEAM_FBREF_ID','COMPETITION','SEASON']]

In [122]:
team_misc_stats.set_index(['COMPETITION', 'SEASON', 'TEAM_NAME'], inplace=True)

In [123]:
team_misc_stats['AERIALS_WON'] = team_aerials_won
team_misc_stats['AERIALS_LOST'] = team_aerials_lost

In [124]:
team_misc_stats.reset_index(inplace=True)
team_misc_stats.drop(columns=['TEAM_NAME'], inplace=True)

In [125]:
upsert_to_snowflake("TEAM_MISC_STATS", team_misc_stats, ['TEAM_FBREF_ID', 'COMPETITION','SEASON'])

[04/26/24 11:50:55] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=940678;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=560236;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=51435;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=580464;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=958008;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=685467;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=808186;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=342011;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=421637;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=992398;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/26/24 11:50:57] INFO     query execution done                                                     ]8;id=88760;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=570598;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS TEAM_MISC_STATS_TEMP]                       ]8;id=465351;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=944188;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=167118;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=993472;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=72066;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=87706;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 96 rows processed.


## Competition, Season and Match Data

In [126]:
df_competitions = fbref_schedule.reset_index()[['COMPETITION', 'SEASON']].drop_duplicates().copy()

In [127]:
df_competitions['COMPETITION_NAME'] = ''
df_competitions['COMPETITION_ACRONYM'] = ''

In [128]:
df_competitions.loc[df_competitions['COMPETITION'] == 'ENG-Premier League', 'COMPETITION_NAME'] = 'English Premier League'
df_competitions.loc[df_competitions['COMPETITION'] == 'ENG-Premier League', 'COMPETITION_ACRONYM'] = 'EPL'

In [129]:
df_competitions

COMPETITION  SEASON        COMPETITION_NAME COMPETITION_ACRONYM
0     ENG-Premier League    2324  English Premier League                 EPL
336          ESP-La Liga    2324                                            
656          FRA-Ligue 1    2324                                            
926       GER-Bundesliga    2324                                            
1196         ITA-Serie A    2324

In [ ]:
# upsert_to_snowflake("COMPETITIONS", df_competitions, ['COMPETITION','SEASON'])

In [137]:
df_seasons = df_competitions[['SEASON']].drop_duplicates().copy()

In [138]:
df_seasons['SEASON_NAME'] = ''
df_seasons['START_YEAR'] = 0
df_seasons['END_YEAR'] = 0

In [139]:
# df_seasons.loc[df_seasons['SEASON'] == 2122, 'SEASON_NAME'] = '2021-2022'
# df_seasons.loc[df_seasons['SEASON'] == 2122, 'START_YEAR'] = 2021
# df_seasons.loc[df_seasons['SEASON'] == 2122, 'END_YEAR'] = 2022
df_seasons.loc[df_seasons['SEASON'] == 2324, 'SEASON_NAME'] = '2023-2024'
df_seasons.loc[df_seasons['SEASON'] == 2324, 'START_YEAR'] = 2023
df_seasons.loc[df_seasons['SEASON'] == 2324, 'END_YEAR'] = 2024

In [140]:
df_seasons

SEASON SEASON_NAME  START_YEAR  END_YEAR
0    2324   2023-2024        2023      2024

In [ ]:
upsert_to_snowflake("SEASONS", df_seasons, ['SEASON'])

In [130]:
df_stadiums = fbref_schedule.reset_index()[['home_team', 'SEASON',
            'venue']].drop_duplicates().rename(columns={'home_team': 'TEAM_NAME', 'venue': 'STADIUM'})

In [131]:
df_stadiums = df_stadiums.merge(team_names, on='TEAM_NAME')[['STADIUM','SEASON','TEAM_FBREF_ID']]

In [140]:
upsert_to_snowflake("STADIUMS", df_stadiums, ['TEAM_FBREF_ID','STADIUM', 'SEASON'])

[04/24/24 19:43:00] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=421261;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=917768;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=508179;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=779192;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=506669;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=569387;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=596205;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=944525;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=968329;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=80685;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/24/24 19:43:03] INFO     query execution done                                                     ]8;id=200853;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=615332;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS STADIUMS_TEMP]                              ]8;id=287459;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=9574;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=222320;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=415383;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=675387;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=465903;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 97 rows processed.


In [132]:
df_matches = fbref_schedule.reset_index()[['game_id', 'date', 'time', 'home_team', 'away_team', 'COMPETITION', 'SEASON', 'venue',
                                           'week', 'day', 'score', 'home_xg', 'away_xg', 'attendance', 'referee', 'ws_game_id']]

In [133]:
df_matches.shape

(1525, 16)

In [134]:
df_matches = df_matches.merge(team_names[['TEAM_FBREF_ID','TEAM_NAME']].rename(columns={'TEAM_FBREF_ID': 'home_team_id', 
                                                         'TEAM_NAME': 'home_team'}), on='home_team', how='left')

In [135]:
df_matches = df_matches.merge(team_names[['TEAM_FBREF_ID','TEAM_NAME']].rename(columns={'TEAM_FBREF_ID': 'away_team_id', 
                                                         'TEAM_NAME': 'away_team'}), on='away_team', how='left')

In [136]:
# Combine df_matches date and time to a dt.datatime configuration
df_matches['date'] = df_matches['date'].astype(str)
df_matches['time'] = df_matches['time'].astype(str)
df_matches['date_time'] = df_matches['date'] + ' ' + df_matches['time']
df_matches['date_time'] = pd.to_datetime(df_matches['date_time'])

In [137]:
# Split score in df_matches by "-" to home_team_score and away_team_score 
df_matches[['home_team_score', 'away_team_score']] = df_matches['score'].str.split('–', expand=True)

In [138]:
df_matches.rename(columns={'game_id': 'MATCH_ID', 'date_time': 'DATE_TIME', 'home_team_id': 'HOME_TEAM_ID', 'away_team_id': 'AWAY_TEAM_ID',
                           'venue': 'STADIUM', 'week': 'GAMEWEEK', 'day': 'DAY','home_team_score': 'HOME_TEAM_SCORE', 
                           'away_team_score':'AWAY_TEAM_SCORE', 'home_xg':'HOME_TEAM_XG','away_xg':'AWAY_TEAM_XG',
                           'attendance':'ATTENDANCE', 'referee': 'REFEREE', 'ws_game_id':'WS_MATCH_ID'}, inplace=True)

In [139]:
df_matches.drop(columns=['date', 'time', 'home_team', 'away_team', 'score'], inplace=True)

In [140]:
df_matches['DATE_TIME'] = df_matches['DATE_TIME'].astype('string')

In [141]:
upsert_to_snowflake("MATCHES", df_matches, ['MATCH_ID'])

[04/26/24 11:51:22] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=406148;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=107232;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=671651;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=123707;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=406373;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=695270;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=321364;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=723615;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=489557;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=642052;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/26/24 11:51:25] INFO     query execution done                                                     ]8;id=480206;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=959625;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS MATCHES_TEMP]                               ]8;id=159005;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=805115;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=837271;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=94643;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=863382;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=107176;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 1525 rows processed.


### Time to deal with event data

In [142]:
# ws_event_spadl = ws.read_events(output_fmt='spadl', match_id=1729409)

In [143]:
ws_event_spadl = ws.read_events(output_fmt='spadl', match_id=game_ids)

[04/26/24 11:51:40] INFO     Scraping game schedule from                                           ]8;id=848208;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=391621;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#428\428]8;;\
                             https://www.whoscored.com/Regions/252/Tournaments/2/Seasons/9618/Engl                 
                             and-Premier-League                                                                    

                    INFO     Scraping game schedule for Tuesday, Apr 2 2024                        ]8;id=935952;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=21059;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

[04/26/24 11:51:41] INFO     Scraping game schedule for Wednesday, Apr 3 2024                      ]8;id=87784;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=325720;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

                    INFO     Scraping game schedule for Thursday, Apr 4 2024                       ]8;id=923363;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=245480;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

[04/26/24 11:51:42] INFO     Scraping game schedule for Saturday, Apr 6 2024                       ]8;id=544254;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=836728;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#328\328]8;;\

...

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\socceraction\spadl\opta.py:219: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  ).bfill()


                    INFO     [9/10] Retrieving game with id=1741296                                ]8;id=832659;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=873697;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#694\694]8;;\

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\socceraction\spadl\opta.py:219: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  ).bfill()


                    INFO     [10/10] Retrieving game with id=1746369                               ]8;id=942939;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py\whoscored.py]8;;\:]8;id=248425;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\whoscored.py#694\694]8;;\

d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\socceraction\spadl\opta.py:219: FutureWarning: Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  ).bfill()


In [144]:
# for i, val in enumerate(game_ids):
#     if i == 0:
#         ws_event_spadl = ws.read_events(output_fmt='spadl', match_id=[val])
#     else:
#         try:
#             ws_event_spadl = pd.concat([ws_event_spadl, ws.read_events(output_fmt='spadl', match_id=[val])])
#         except:
#             print(i, val)

In [145]:
len(ws_event_spadl['game_id'].unique())

10

In [146]:
game_ids

array([1729409, 1729418, 1729421, 1729429, 1729435, 1729412, 1741294,
       1741293, 1741296, 1746369], dtype=int64)

In [147]:
ws_event_spadl.to_csv('ws_event_spadl_hold.csv')
# ws_event_spadl = pd.read_csv('ws_event_spadl_hold.csv', index_col=0)

In [148]:
ws_event_spadl.loc[ws_event_spadl['team'] == 'Atletico', 'team'] = 'Atlético Madrid'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Deportivo Alaves', 'team'] = 'Alavés'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Cadiz', 'team'] = 'Cádiz'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Real Betis', 'team'] = 'Betis'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Real Valladolid', 'team'] = 'Valladolid'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Almeria', 'team'] = 'Almería'

ws_event_spadl.loc[ws_event_spadl['team'] == 'Arminia Bielefeld', 'team'] = 'Arminia'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Bayern', 'team'] = 'Bayern Munich'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Borussia Dortmund', 'team'] = 'Dortmund'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Borussia M.Gladbach', 'team'] = "M'Gladbach"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Eintracht Frankfurt', 'team'] = "Eint Frankfurt"
ws_event_spadl.loc[ws_event_spadl['team'] == 'FC Koln', 'team'] = 'Köln'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Mainz', 'team'] = "Mainz 05"
ws_event_spadl.loc[ws_event_spadl['team'] == 'RBL', 'team'] = "RB Leipzig"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Greuther Fuerth', 'team'] = "Greuther Fürth"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Hertha Berlin', 'team'] = "Hertha BSC"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Schalke', 'team'] = 'Schalke 04'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Darmstadt', 'team'] = 'Darmstadt 98'
ws_event_spadl.loc[ws_event_spadl['team'] == 'FC Heidenheim', 'team'] = 'Heidenheim'

ws_event_spadl.loc[ws_event_spadl['team'] == 'Verona', 'team'] = 'Hellas Verona'

ws_event_spadl.loc[ws_event_spadl['team'] == 'PSG', 'team'] = "Paris S-G"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Saint-Etienne', 'team'] = "Saint-Étienne"
ws_event_spadl.loc[ws_event_spadl['team'] == 'AC Ajaccio', 'team'] = "Ajaccio"

ws_event_spadl.loc[ws_event_spadl['team'] == 'Manchester United', 'team'] = 'Manchester Utd'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Newcastle United', 'team'] = 'Newcastle Utd'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Newcastle', 'team'] = 'Newcastle Utd'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Tottenham Hotspur', 'team'] = 'Tottenham'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Wolverhampton Wanderers', 'team'] = 'Wolves'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Wolverhampton', 'team'] = 'Wolves'
ws_event_spadl.loc[ws_event_spadl['team'] == 'Nottingham Forest', 'team'] = "Nott'ham Forest"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Leicester', 'team'] = "Leicester City"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Leeds', 'team'] = "Leeds United"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Sheffield United', 'team'] = "Sheffield Utd"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Sheff Utd', 'team'] = "Sheffield Utd"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Luton', 'team'] = "Luton Town"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Norwich', 'team'] = "Norwich City"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Man City', 'team'] = "Manchester City"
ws_event_spadl.loc[ws_event_spadl['team'] == 'Man Utd', 'team'] = "Manchester Utd"

In [149]:
ws_event_spadl.shape

(16908, 16)

In [150]:
ws_event_spadl = ws_event_spadl.merge(spadl.actiontypes_df(), how="left").merge(spadl.bodyparts_df(), how="left")

In [151]:
ws_event_spadl.rename({'game_id':'WS_MATCH_ID', 'original_event_id':'ORIGINAL_EVENT_ID','period_id':'PERIOD_ID',
                       'time_seconds':'TIME_SECONDS', 'team_id':'TEAM_WS_ID', 'player_id':'PLAYER_WS_ID', 'start_x':'START_X',
                        'end_x':'END_X', 'start_y':'START_Y', 'end_y':'END_Y','type_name':'TYPE_NAME',
                        'bodypart_name':'BODYPART_NAME','result_id':'RESULT_ID', 'action_id':'ACTION_ID'}, axis=1, inplace=True)

In [152]:
ws_event_spadl = ws_event_spadl.merge(df_matches[['MATCH_ID', 'WS_MATCH_ID']], on='WS_MATCH_ID')

In [153]:
ws_event_spadl = ws_event_spadl.merge(curr_team_names[['TEAM_FBREF_ID','TEAM_WS_ID']], on='TEAM_WS_ID')

In [154]:
ws_event_spadl.rename({'TEAM_FBREF_ID':'team_id','START_X':'start_x','START_Y':'start_y','END_X':'end_x','END_Y':'end_y'}, axis=1,
                      inplace=True)

In [155]:
df_matches_left =df_matches[df_matches['MATCH_ID'].isin(ws_event_spadl['MATCH_ID'].unique())]

In [156]:
# df_matches_left = df_matches[df_matches['MATCH_ID'].isin(matches_to_scarpe)]

In [157]:
for index, row in df_matches_left.iterrows():
    inds_to_replace = ws_event_spadl[ws_event_spadl['MATCH_ID'] == row['MATCH_ID']].index
    ws_event_spadl.loc[inds_to_replace] = spadl.play_left_to_right(ws_event_spadl.loc[inds_to_replace], row['HOME_TEAM_ID'])

In [158]:
ws_event_spadl['NEW_TIME_SECONDS'] = ws_event_spadl['TIME_SECONDS']

In [159]:
ws_event_spadl_period1 = ws_event_spadl[ws_event_spadl['PERIOD_ID'] == 1]
ws_event_spadl_period2 = ws_event_spadl[ws_event_spadl['PERIOD_ID'] == 2]

In [160]:
start_time_2nd_half = ws_event_spadl_period2.groupby(['MATCH_ID', 'PERIOD_ID'])['NEW_TIME_SECONDS'].min().reset_index()

In [161]:
for index, row in tqdm(start_time_2nd_half.iterrows()):
    time_to_remove = row['NEW_TIME_SECONDS']
    ws_event_spadl.loc[(ws_event_spadl['MATCH_ID'] == row['MATCH_ID']) & (ws_event_spadl['PERIOD_ID'] == 2), 'NEW_TIME_SECONDS'] -= time_to_remove

10it [00:00, 454.54it/s]


In [162]:
ws_event_spadl.rename({'start_x':'START_X','end_x':'END_X','start_y':'START_Y','end_y':'END_Y',
                       'team_id':'TEAM_FBREF_ID'}, axis=1, inplace=True)

In [163]:
ws_event_spadl.shape

(16908, 21)

In [164]:
events_drop_inds = ws_event_spadl[ws_event_spadl[['WS_MATCH_ID', 'PLAYER_WS_ID','ACTION_ID']].duplicated()].index

In [165]:
len(events_drop_inds)

0

In [166]:
ws_event_spadl = ws_event_spadl.drop(events_drop_inds)

In [167]:
upsert_to_snowflake("EVENTS_SPADL", 
                    ws_event_spadl.drop(['type_id', 'player', 'team', 'WS_MATCH_ID', 'TEAM_WS_ID','bodypart_id'],axis=1), 
                    ['MATCH_ID','ACTION_ID'])

[04/26/24 13:19:51] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=58622;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=267057;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

[04/26/24 13:19:52] INFO     query execution done                                                     ]8;id=970429;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=957894;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=535437;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=61298;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=282857;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=978777;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=584174;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=714506;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/26/24 13:19:57] INFO     query execution done                                                     ]8;id=336014;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=187311;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS EVENTS_SPADL_TEMP]                          ]8;id=966929;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=881422;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=709416;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=741188;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=106024;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=91282;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 16908 rows processed.


In [168]:
# cur.execute('SELECT * FROM EVENTS_SPADL')
# events_rows = cur.fetchall()
# column_names = [desc[0] for desc in cur.description]
# ws_event_spadl = pd.DataFrame(events_rows, columns=column_names)

### Update the "Players" table in Snowflake

In [169]:
## Sort out "Players" "Table
ws_players.rename({'team_id':'TEAM_WS_ID', 'game_id':'WS_MATCH_ID'}, axis=1, inplace=True)

In [170]:
ws_players = ws_players.merge(curr_team_names, on="TEAM_WS_ID", how="left")

In [171]:
ws_players = ws_players.sort_values(by=["WS_MATCH_ID","TEAM_NAME","jersey_number"])

In [172]:
fbref_lineups.shape

(407, 6)

In [173]:
fbref_lineups = fbref_lineups.reset_index().merge(fbref_schedule.reset_index()[['game', 'game_id',
                                                                                'ws_game_id']], how='inner', on='game')

In [174]:
fbref_lineups = fbref_lineups.rename({'ws_game_id':'WS_MATCH_ID'}, axis=1)

In [175]:
fbref_lineups.shape

(407, 11)

In [176]:
fbref_lineups = fbref_lineups.merge(curr_team_names[['TEAM_NAME','TEAM_FBREF_ID','TEAM_WS_ID']], on='TEAM_NAME')

In [177]:
ws_players.rename({'player_id':'WS_player_id', 'player_name':'WS_player_name','minutes_played':'WS_minutes_played',
                   'starting_position':'WS_starting_position', 'is_starter':'WS_is_starter'}, axis=1, inplace=True)

In [178]:
fbref_lineups.rename({'minutes_played':'FBREF_minutes_played', 'game_id':'MATCH_ID','position':'FBREF_position',
                      'is_starter':'FBREF_is_starter'}, axis=1, inplace=True)

In [179]:
fbref_lineups = fbref_lineups.merge(ws_players, on=["TEAM_FBREF_ID", "TEAM_NAME", "WS_MATCH_ID",
                                                    "TEAM_WS_ID", "jersey_number"], how="left")

In [180]:
df_players = fbref_lineups[['WS_player_id', 'player', 'WS_player_name']].drop_duplicates()

In [181]:
df_players = df_players.dropna(subset=['WS_player_id'])

In [182]:
df_players.rename({'WS_player_id':'PLAYER_WS_ID', 'player':'PLAYER_FBREF_NAME', 'WS_player_name':'PLAYER_WS_NAME'}, 
                  axis=1, inplace=True)

In [183]:
df_players[df_players['PLAYER_WS_ID'].duplicated()]

Empty DataFrame
Columns: [PLAYER_WS_ID, PLAYER_FBREF_NAME, PLAYER_WS_NAME]
Index: []

In [184]:
df_players = df_players.replace('Ronald Araujo', 'Ronald Araújo')
df_players = df_players.replace('Íñigo Martínez', 'Iñigo Martínez')

In [185]:
df_players = df_players.replace('Lucas Michel', 'Lucas Michal')
df_players = df_players.replace('Théo Ramousse', 'Théo Borne')
df_players = df_players.replace('Joel Mugisha', 'Joel Mvuka')

In [186]:
df_players = df_players[(df_players['PLAYER_FBREF_NAME'] != 'Destiny Egharevba') | (df_players['PLAYER_WS_ID'] != 428502)]

In [187]:
df_players = df_players[(df_players['PLAYER_FBREF_NAME'] != 'Sacha Delaye') | (df_players['PLAYER_WS_NAME'] != 'Enzo Tchato')]

In [188]:
df_players = df_players.replace('Malcolm Barcola', 'Bradley Barcola')

In [189]:
df_players = df_players[['PLAYER_WS_ID', 'PLAYER_FBREF_NAME', 'PLAYER_WS_NAME']].drop_duplicates()

In [190]:
# df_players[df_players['PLAYER_WS_ID']==426915]

In [191]:
## Find all instances of "Min-Jae Kim" in df_players

# df_players[df_players['PLAYER_FBREF_NAME'].str.contains('Luca Ravanelli')]

# # Replace it with "Kim Min-Jae"

# df_players.loc[df_players['PLAYER_WS_ID'] == 426915, 'PLAYER_FBREF_NAME'] = 'Felix Afena-Gyan'

In [192]:
upsert_to_snowflake("PLAYERS", df_players, ['PLAYER_WS_ID'])

[04/26/24 13:20:36] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=465302;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=251437;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=469663;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=792;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=942326;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=608031;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=207287;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=126158;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=496926;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=37811;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/26/24 13:20:39] INFO     query execution done                                                     ]8;id=84521;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=306450;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS PLAYERS_TEMP]                               ]8;id=936017;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=159570;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=86130;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=110049;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=289147;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=395569;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 407 rows processed.


Player-match combos now

In [193]:
df_player_match = fbref_lineups[['WS_player_id', 'player','MATCH_ID', 'TEAM_FBREF_ID', 'WS_starting_position', 
                                 'FBREF_position','jersey_number','FBREF_minutes_played','FBREF_is_starter','WS_is_starter',
                                 'WS_minutes_played']]

In [194]:
df_player_match = df_player_match.rename({'WS_player_id':'PLAYER_WS_ID', 'player':'PLAYER_FBREF_NAME', 'WS_starting_position':'STARTING_POSITION_WS',
                        'FBREF_position':'POSITION_FBREF', 'jersey_number':'JERSEY_NUMBER', 'FBREF_minutes_played':'MINUTES_PLAYED_FBREF',
                        'FBREF_is_starter':'IS_STARTER_FBREF','WS_is_starter':'IS_STARTER_WS','WS_minutes_played':'MINUTES_PLAYED_WS'}, axis=1)

In [195]:
inds_to_drop = df_player_match[df_player_match[['PLAYER_WS_ID', 'MATCH_ID']].duplicated()].index

In [196]:
inds_to_drop

Index([], dtype='int64')

In [197]:
df_player_match = df_player_match.drop(inds_to_drop)

In [198]:
df_player_match = df_player_match.dropna(subset=['PLAYER_WS_ID'])

In [199]:
df_player_match = df_player_match[~((df_player_match['MATCH_ID'] == 'd6d3de2f') & 
                                    (df_player_match['PLAYER_WS_ID'] == 502424))]

In [200]:
df_player_match = df_player_match[~((df_player_match['MATCH_ID'] == '1a0a12f3') & 
                                    (df_player_match['PLAYER_WS_ID'] == 135328))]

In [201]:
upsert_to_snowflake("PLAYER_MATCH", df_player_match, ['PLAYER_WS_ID', 'MATCH_ID'])

[04/26/24 13:20:46] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=765437;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=53326;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

                    INFO     query execution done                                                     ]8;id=758959;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=654950;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=159337;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=766723;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=142591;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=831286;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

                    INFO     query execution done                                                     ]8;id=517626;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=301194;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

...

[04/26/24 13:20:49] INFO     query execution done                                                     ]8;id=968539;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=818373;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS PLAYER_MATCH_TEMP]                          ]8;id=444810;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=977460;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=923658;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=242342;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=200148;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=464541;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 407 rows processed.


### Add Shot Event Data

In [202]:
no_shot_match = []

In [203]:
matches_to_scarpe1 = df_matches[df_matches['MATCH_ID'].isin(ws_event_spadl['MATCH_ID'].unique())]['MATCH_ID']

In [204]:
len(matches_to_scarpe1)

10

In [205]:
for i, val in tqdm(enumerate(matches_to_scarpe1)):
    if i == 0:
        fbref_shot_events = fbref.read_shot_events(match_id=val)
    else:
        try:
            fbref_shot_events = pd.concat([fbref_shot_events, fbref.read_shot_events(match_id=val)])
        except:
            no_shot_match.append(val)

0it [00:00, ?it/s]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 13:22:04] INFO     [1/1] Retrieving game with id=3435dfcc                                   ]8;id=26923;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=897214;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1063\1063]8;;\

1it [00:56, 56.10s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 13:23:00] INFO     [1/1] Retrieving game with id=ee21eba2                                   ]8;id=879050;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=920217;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1063\1063]8;;\

2it [01:50, 55.09s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


...

8it [07:19, 54.84s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 13:29:24] INFO     [1/1] Retrieving game with id=88182e5f                                   ]8;id=550846;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=9454;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1063\1063]8;;\

9it [08:14, 54.86s/it]d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py:680: FutureWarning: The behavior of DataFrame concatenation with empty or all-NA entries is deprecated. In a future version, this will no longer exclude empty or all-NA columns when determining the result dtypes. To retain the old behavior, exclude the relevant entries before the concat operation.
  pd.concat(schedule)


[04/26/24 13:30:19] INFO     [1/1] Retrieving game with id=bca64d25                                   ]8;id=478240;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py\fbref.py]8;;\:]8;id=24965;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\soccerdata\fbref.py#1063\1063]8;;\

10it [09:10, 55.00s/it]


In [206]:
no_shot_match

[]

In [207]:
fbref_shot_events = fbref_shot_events.rename_axis(index={'season': 'SEASON', 'league': 'COMPETITION'})

In [208]:
len(fbref_shot_events)

297

In [209]:
fbref_shot_events = make_season_integer(fbref_shot_events)

In [210]:
ws_event_spadl['TIME_SECONDS'] = ws_event_spadl['TIME_SECONDS'].astype(int)
ws_event_spadl['PLAYER_WS_ID'] = ws_event_spadl['PLAYER_WS_ID'].astype(int)

In [211]:
fbref_shot_events.shape

(297, 13)

In [212]:
ws_shots = ws_event_spadl[(ws_event_spadl['TYPE_NAME'] == 'shot') | (ws_event_spadl['TYPE_NAME'] == 'shot_freekick') | \
               (ws_event_spadl['TYPE_NAME'] == 'shot_penalty')]

In [213]:
ws_shots.shape

(290, 21)

In [214]:
fbref_shot_events.reset_index(inplace=True)

In [215]:
fbref_shot_events.columns = fbref_shot_events.columns.get_level_values(0) + fbref_shot_events.columns.get_level_values(1)

In [216]:
fbref_shot_events.to_csv('fbref_shot_events.csv')
# fbref_shot_events = pd.read_csv('fbref_shot_events.csv', index_col=0)

In [217]:
fbref_shot_events = fbref_shot_events.merge(fbref_schedule[['COMPETITION','SEASON','game','game_id','ws_game_id']], 
                        on=['COMPETITION','SEASON','game'])

In [218]:
fbref_shot_events.rename({'player':'PLAYER_FBREF_NAME', 'game_id':'MATCH_ID'}, axis=1, inplace=True)

In [219]:
fbref_shot_events['PLAYER_FBREF_NAME'] = fbref_shot_events['PLAYER_FBREF_NAME'].str.replace(' \(pen\)', '', regex=True)

In [220]:
fbref_shot_events.loc[fbref_shot_events['PLAYER_FBREF_NAME'] == 'Loum Ndiaye', 'PLAYER_FBREF_NAME'] = "Mamadou N'Diaye"

In [221]:
len(df_player_match['MATCH_ID'].unique())

10

In [222]:
df_player_match = df_player_match[~((df_player_match['MATCH_ID'] == 'd6d3de2f') & 
                                    (df_player_match['PLAYER_WS_ID'] == 502424))]
df_player_match = df_player_match[~((df_player_match['MATCH_ID'] == '1a0a12f3') & 
                                    (df_player_match['PLAYER_WS_ID'] == 135328))]

In [223]:
fbref_shot_events = fbref_shot_events.merge(df_player_match[['PLAYER_WS_ID', 'PLAYER_FBREF_NAME', 'MATCH_ID']], 
                        on=['PLAYER_FBREF_NAME', 'MATCH_ID'], how="inner")

In [224]:
fbref_shot_events = fbref_shot_events[(fbref_shot_events['MATCH_ID'] != '7e4bbae4') | 
                  (fbref_shot_events['PLAYER_FBREF_NAME'] != 'Borja Iglesias')]

In [225]:
fbref_shot_events = fbref_shot_events[(fbref_shot_events['MATCH_ID'] != '7e4bbae4') | 
                  (fbref_shot_events['PLAYER_FBREF_NAME'] != 'Roberto González')]

In [226]:
fbref_shot_events = fbref_shot_events[(fbref_shot_events['MATCH_ID'] != '82b8a000') |  (fbref_shot_events['minute'] != '81')]

In [227]:
fbref_shot_events = fbref_shot_events[(fbref_shot_events['MATCH_ID'] != '9bd36df7') |  
                                      (fbref_shot_events['PLAYER_FBREF_NAME'] != 'Saîf-Eddine Khaoui') |
                                      (fbref_shot_events['minute'] != '38')]

In [228]:
fbref_shot_events = fbref_shot_events[(fbref_shot_events['MATCH_ID'] != 'f7d8a40e') |  
                                      (fbref_shot_events['PLAYER_FBREF_NAME'] != 'Matteo Prati') |
                                      (fbref_shot_events['minute'] != '77')]

In [229]:
# fbref_shot_events = fbref_shot_events.merge(df_players, on='PLAYER_FBREF_NAME', how="left")

In [230]:
# ws_shots = ws_event_spadl[(ws_event_spadl['TYPE_NAME'] == 'shot') | (ws_event_spadl['TYPE_NAME'] == 'shot_freekick') | \
#                (ws_event_spadl['TYPE_NAME'] == 'shot_penalty')]

In [231]:
ws_shots['ORIGINAL_EVENT_ID'] = ws_shots['ORIGINAL_EVENT_ID'].astype(float)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\976316004.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  ws_shots['ORIGINAL_EVENT_ID'] = ws_shots['ORIGINAL_EVENT_ID'].astype(float)


In [232]:
ws_shots = ws_shots.drop_duplicates()

In [233]:
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != '7e4bbae4')| 
        (ws_shots['player'] != 'Rober')]

In [234]:
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != '7e4bbae4')| 
        (ws_shots['player'] != 'Borja Iglesias')]

In [235]:
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != '47134469')| 
        (ws_shots['player'] != 'Ángel Alarcón')]

In [236]:
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != 'c34bbc21')]

In [237]:
# ws_dropped_shots = ws_shots[ws_shots['PLAYER_WS_ID'] == 444304]
# ws_shots = ws_shots[ws_shots['PLAYER_WS_ID'] != 444304]

In [238]:
## Bamba from Lorient's shots to be dropped
ws_dropped_shots = ws_shots[ws_shots['PLAYER_WS_ID'] == 515493]
ws_shots = ws_shots[ws_shots['PLAYER_WS_ID'] != 515493]

In [239]:
ws_shots = ws_shots[ws_shots['PLAYER_WS_ID'] != 509340]
ws_shots = ws_shots[ws_shots['PLAYER_WS_ID'] != 511120]
ws_shots = ws_shots[ws_shots['PLAYER_WS_ID'] != 492362]

In [240]:
fbref_shot_events.shape

(296, 19)

In [241]:
ws_shots.shape

(288, 21)

In [242]:
## Rogue Joel Veltman shot should be dropped
ws_shots = ws_shots.drop(ws_shots[(ws_shots['PLAYER_WS_ID'] == 110290) & 
                                  (ws_shots['MATCH_ID'] == '36be5cee')].index)

In [243]:
## Rogue Negredo shot to drop
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != 'c409c152') | (ws_shots['PLAYER_WS_ID'] != 23757) | (ws_shots['ACTION_ID'] != 149)]

In [244]:
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != '84765ee6') | (ws_shots['ACTION_ID'] != 117)]

In [245]:
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != 'b63b2da7') | (ws_shots['WS_MATCH_ID'] != 1727122)]

In [246]:
## Rogue Negredo shot to drop
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != 'de22618d') | (ws_shots['PLAYER_WS_ID'] != 286828) | (ws_shots['ACTION_ID'] != 1716)]

In [247]:
## Rogue Rodrigo Riquelme shot to drop
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != 'bccce279') | (ws_shots['PLAYER_WS_ID'] != 382631) | (ws_shots['ACTION_ID'] != 958)]

In [248]:
## Rogue Rodrigo Riquelme shot to drop
ws_shots = ws_shots[(ws_shots['MATCH_ID'] != '55996670') | (ws_shots['PLAYER_WS_ID'] != 403649) | (ws_shots['ACTION_ID'] != 1229)]

In [249]:
relevant_inds = fbref_shot_events.drop(['ws_game_id', 'PLAYER_WS_ID'], axis=1).drop_duplicates().index
relevant_inds

RangeIndex(start=0, stop=296, step=1)

In [250]:
fbref_shot_events = fbref_shot_events.loc[list(relevant_inds)]

In [251]:
# Get the indices of the last 5 rows where MATCH_ID == '4c975b7e'
indices = fbref_shot_events[fbref_shot_events['MATCH_ID'] == '4c975b7e'].index[-5:]
fbref_shot_events = fbref_shot_events.drop(indices)

In [261]:
fbref_shot_events.shape

(269, 19)

In [262]:
ws_shots.shape

(269, 21)

In [263]:
for game in ws_shots['MATCH_ID'].unique():
    if len(ws_shots.loc[ws_shots.MATCH_ID == game]) != len(fbref_shot_events.loc[fbref_shot_events.MATCH_ID == game]):
        print(game)

In [264]:
# fbref_shot_events[['new_minute', 'added_minute']] = fbref_shot_events['minute'].apply(
#     lambda x: pd.Series(str(x).split('+') if '+' in str(x) else [x, 0])
# )

In [265]:
# fbref_shot_events['new_minute'] = fbref_shot_events['new_minute'].astype(int)
# fbref_shot_events['added_minute'] = fbref_shot_events['added_minute'].astype(int)

In [266]:
# fbref_shot_events = fbref_shot_events.sort_values(by=['MATCH_ID', 'new_minute', 'added_minute', 'PLAYER_WS_ID']).reset_index(drop=True)

In [267]:
ws_shots = ws_shots.sort_values(by=['MATCH_ID', 'PERIOD_ID','ACTION_ID']).reset_index(drop=True)

In [268]:
ws_shots['xG'] = np.nan
ws_shots['PSxG'] = np.nan
ws_shots['outcome'] = np.nan
ws_shots['distance'] = np.nan
ws_shots['body_part'] = np.nan
ws_shots['notes'] = np.nan
ws_shots['SCA 1player'] = np.nan
ws_shots['SCA 1event'] = np.nan
ws_shots['SCA 2player'] = np.nan
ws_shots['SCA 2event'] = np.nan
ws_shots['FBREF_PLAYER_WS_ID'] = np.nan
ws_shots['PLAYER_WS_NAME'] = np.nan

In [269]:
fbref_shot_events.rename({'PLAYER_WS_ID':'FBREF_PLAYER_WS_ID'}, axis=1, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\2543053858.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  fbref_shot_events.rename({'PLAYER_WS_ID':'FBREF_PLAYER_WS_ID'}, axis=1, inplace=True)


In [270]:
fbref_shot_events = fbref_shot_events.merge(df_players.rename({'PLAYER_WS_ID':'FBREF_PLAYER_WS_ID'}, axis=1), 
                        on=['FBREF_PLAYER_WS_ID', 'PLAYER_FBREF_NAME'], how="left")

In [271]:
cols_of_interest = ['xG', 'PSxG', 'outcome', 'distance', 'body_part', 'notes', 'SCA 1player', 'SCA 1event', 
                    'SCA 2player', 'SCA 2event', 'FBREF_PLAYER_WS_ID', 'PLAYER_WS_NAME']
for game in ws_shots['MATCH_ID'].unique():
    df_hold = fbref_shot_events[fbref_shot_events['MATCH_ID'] == game]
    ind_list = ws_shots[ws_shots['MATCH_ID'] == game].index
    ws_shots.loc[ind_list, cols_of_interest] = np.array(df_hold[cols_of_interest])

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\3612877618.py:6: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '[<NA>, 0.58, <NA>, <NA>, 0.29, <NA>, <NA>, <NA>, <NA>, 0.06, 0.13, <NA>, 0.99, 0.28, <NA>, <NA>, 0.35, <NA>, <NA>, <NA>, 0.03]' has dtype incompatible with float64, please explicitly cast to a compatible dtype first.
  ws_shots.loc[ind_list, cols_of_interest] = np.array(df_hold[cols_of_interest])
C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\3612877618.py:6: FutureWarning: Setting an item of incompatible dtype is deprecated and will raise an error in a future version of pandas. Value '['Off Target', 'Goal', 'Off Target', 'Off Target', 'Goal', 'Blocked', 'Off Target', 'Blocked', 'Blocked', 'Saved', 'Saved', 'Blocked', 'Goal', 'Goal', 'Blocked', 'Off Target', 'Saved', 'Blocked', 'Off Target', 'Woodwork', 'Saved']' has dtype incompatible with float64, please explicitly cast to a compatible dt

In [272]:
ws_shots['FBREF_PLAYER_WS_ID'] = ws_shots['FBREF_PLAYER_WS_ID'].astype(int)

In [279]:
mismatched_inds = ws_shots[ws_shots['PLAYER_WS_ID'] != ws_shots['FBREF_PLAYER_WS_ID']].index

In [280]:
mismatched_inds

Index([], dtype='int64')

In [275]:
# ONLY for the indecies with mismatched_inds, cahnge "FBREF_PLAYER_WS_ID" to teh value in "PLAYER_WS_ID" if "player" column's value is equal to "PLAYER_WS_NAME" column's value
mask = ws_shots.loc[mismatched_inds, 'player'] == ws_shots.loc[mismatched_inds, 'PLAYER_WS_NAME']
ws_shots.loc[mismatched_inds[mask], 'FBREF_PLAYER_WS_ID'] = ws_shots.loc[mismatched_inds[mask], 'PLAYER_WS_ID']

In [276]:
mismatched_inds = ws_shots[ws_shots['PLAYER_WS_ID'] != ws_shots['FBREF_PLAYER_WS_ID']].index

In [277]:
mask = (ws_shots.loc[mismatched_inds, 'player'] == 'Vítinha')
ws_shots.loc[mismatched_inds[mask], 'FBREF_PLAYER_WS_ID'] = ws_shots.loc[mismatched_inds[mask], 'PLAYER_WS_ID']

In [278]:
for i in range(len(mismatched_inds) // 2):
    val1 = ws_shots.loc[mismatched_inds, cols_of_interest].iloc[2*i]
    val2 = ws_shots.loc[mismatched_inds, cols_of_interest].iloc[(2*i)+1]

    ws_shots.loc[val1.name, cols_of_interest] = np.array(val2)
    ws_shots.loc[val2.name, cols_of_interest] = np.array(val1)

In [281]:
#### Remove this part later becasue it's just for Yarmolyuik

df_shots = ws_shots[['MATCH_ID','ACTION_ID','xG', 'PSxG', 'outcome', 'distance', 
          'body_part', 'notes', 'SCA 1player', 'SCA 1event', 'SCA 2player', 'SCA 2event']]

# ws_dropped_shots[[cols_of_interest]] = np.nan

# rows_to_add = [
#     [0.04,np.nan,'Blocked',16,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
# [0.03,0.12,'Saved',27,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
# [0.05,np.nan,'Off Target',21,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
# [0.49,0.25,'Saved',11,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
# [0.09,np.nan,'Off Target',8,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk'],
# [0.02,0.02,'Saved',19,'Right Foot',np.nan,np.nan,np.nan,np.nan,np.nan,444304,'Yehor Yarmoliuk']
# ]

# ws_dropped_shots[cols_of_interest] = np.array(rows_to_add)

In [282]:
# df_shots = pd.concat([df_shots, ws_dropped_shots[['MATCH_ID','ACTION_ID','xG', 'PSxG', 'outcome', 'distance', 
#           'body_part', 'notes', 'SCA 1player', 'SCA 1event', 'SCA 2player', 'SCA 2event']]]).sort_index()

In [283]:
# df_shots.replace({"Jarrell Quansah": "Jarell Quansah"}, inplace=True)
# df_shots.replace({"Omotayo Adaramola": "Tayo Adaramola"}, inplace=True)

In [284]:
df_shots.rename({'xG':'XG', 'PSxG':'PSXG', 'outcome':'OUTCOME', 'distance':'DISTANCE', 'body_part':'BODY_PART',
                 'notes':'NOTES', 'SCA 1player':'SCA_1_PLAYER_FBREF_NAME', 'SCA 1event':'SCA_1_PLAYER_FBREF_EVENT',
                 'SCA 2player':'SCA_2_PLAYER_FBREF_NAME', 'SCA 2event':'SCA_2_PLAYER_FBREF_EVENT'}, axis=1, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\2795869585.py:1: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  df_shots.rename({'xG':'XG', 'PSxG':'PSXG', 'outcome':'OUTCOME', 'distance':'DISTANCE', 'body_part':'BODY_PART',


In [285]:
# df_players.rename({'PLAYER_FBREF_NAME':'SCA_1_PLAYER_FBREF_NAME'}, axis=1, inplace=True)
# df_players.rename({'PLAYER_WS_ID':'SCA_1_PLAYER_FBREF_ID'}, axis=1, inplace=True)

In [286]:
df_player_match.rename({'PLAYER_FBREF_NAME':'SCA_1_PLAYER_FBREF_NAME'}, axis=1, inplace=True)
df_player_match.rename({'PLAYER_WS_ID':'SCA_1_PLAYER_FBREF_ID'}, axis=1, inplace=True)

In [287]:
df_shots.loc[df_shots['SCA_1_PLAYER_FBREF_NAME'] == 'Loum Ndiaye', 'SCA_1_PLAYER_FBREF_NAME'] = "Mamadou N'Diaye"

In [288]:
df_shots.shape

(269, 12)

In [289]:
df_shots = df_shots.merge(df_player_match[['SCA_1_PLAYER_FBREF_ID','SCA_1_PLAYER_FBREF_NAME','MATCH_ID']], 
                          on=['SCA_1_PLAYER_FBREF_NAME','MATCH_ID'], how='left')

In [290]:
relevant_inds = df_shots[['SCA_1_PLAYER_FBREF_NAME', 'MATCH_ID', 'ACTION_ID']].drop_duplicates().index

In [291]:
df_shots = df_shots.loc[relevant_inds]

In [292]:
# df_shots = df_shots.merge(df_players[['SCA_1_PLAYER_FBREF_ID','SCA_1_PLAYER_FBREF_NAME']], on='SCA_1_PLAYER_FBREF_NAME', how='left')

In [293]:
# df_players.rename({'SCA_1_PLAYER_FBREF_NAME':'SCA_2_PLAYER_FBREF_NAME'}, axis=1, inplace=True)
# df_players.rename({'SCA_1_PLAYER_FBREF_ID':'SCA_2_PLAYER_FBREF_ID'}, axis=1, inplace=True)

df_player_match.rename({'SCA_1_PLAYER_FBREF_NAME':'SCA_2_PLAYER_FBREF_NAME'}, axis=1, inplace=True)
df_player_match.rename({'SCA_1_PLAYER_FBREF_ID':'SCA_2_PLAYER_FBREF_ID'}, axis=1, inplace=True)

In [294]:
# df_shots = df_shots.merge(df_players[['SCA_2_PLAYER_FBREF_ID','SCA_2_PLAYER_FBREF_NAME']], on='SCA_2_PLAYER_FBREF_NAME', how='left')
df_shots = df_shots.merge(df_player_match[['SCA_2_PLAYER_FBREF_ID','SCA_2_PLAYER_FBREF_NAME','MATCH_ID']], 
                          on=['SCA_2_PLAYER_FBREF_NAME','MATCH_ID'], how='left')

In [295]:
relevant_inds = df_shots[['SCA_2_PLAYER_FBREF_NAME', 'MATCH_ID', 'ACTION_ID']].drop_duplicates().index

In [296]:
df_shots = df_shots.loc[relevant_inds]

In [297]:
inds_to_drop = (df_shots[df_shots[['MATCH_ID', 'ACTION_ID']].duplicated()].index)

In [298]:
inds_to_drop

Index([], dtype='int64')

In [299]:
df_shots = df_shots.drop(inds_to_drop)

In [300]:
df_shots = df_shots.drop(['SCA_1_PLAYER_FBREF_NAME', 'SCA_2_PLAYER_FBREF_NAME'], axis=1)

In [301]:
df_shots.rename({'SCA_1_PLAYER_FBREF_ID':'SCA_1_PLAYER_WS_ID', 'SCA_2_PLAYER_FBREF_ID':'SCA_2_PLAYER_WS_ID'}, 
                axis=1, inplace=True)

In [302]:
df_shots.replace({pd.NA: np.nan}, inplace=True)

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\3696910441.py:1: FutureWarning: Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`
  df_shots.replace({pd.NA: np.nan}, inplace=True)


In [303]:
df_shots['XG'] = df_shots['XG'].astype(float)
df_shots['PSXG'] = df_shots['PSXG'].astype(float)
df_shots['DISTANCE'] = df_shots['DISTANCE'].astype(int)

In [304]:
df_shots.shape

(269, 12)

In [305]:
upsert_to_snowflake("SHOT_EVENTS", df_shots, ['MATCH_ID', 'ACTION_ID'])

C:\Users\ksbha\AppData\Local\Temp\ipykernel_27548\138046206.py:6: UserWarning: Pandas Dataframe has non-standard index of type <class 'pandas.core.indexes.base.Index'> which will not be written. Consider changing the index to pd.RangeIndex(start=0,...,step=1) or call reset_index() to keep index as column(s)
  success, nchunks, nrows, _ = write_pandas(conn, dataframe, temp_table_name, auto_create_table=True)


[04/26/24 17:02:11] INFO     query: [CREATE TEMP STAGE /*                                             ]8;id=107872;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=225296;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             Python:snowflake.connector.pandas_tools.write_pandas() */ "...]                       

[04/26/24 17:02:12] INFO     query execution done                                                     ]8;id=61959;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=157075;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=133072;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=679979;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

                    INFO     query: [PUT /* Python:snowflake.connector.pandas_tools.write_pandas() */ ]8;id=96620;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=269392;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\
                             'file://C:\\Use...]                                                                   

...

[04/26/24 17:02:17] INFO     query execution done                                                     ]8;id=63089;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=253401;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     query: [DROP TABLE IF EXISTS SHOT_EVENTS_TEMP]                           ]8;id=573511;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=629585;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#833\833]8;;\

                    INFO     query execution done                                                     ]8;id=704792;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=482804;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#846\846]8;;\

                    INFO     Number of results in first chunk: 1                                      ]8;id=362444;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py\cursor.py]8;;\:]8;id=38956;file://d:\Users\ksbha\miniconda3\envs\footy\Lib\site-packages\snowflake\connector\cursor.py#988\988]8;;\

Upsert completed. 269 rows processed.


In [ ]:
## DF SHOTS NEEDS SOME CLEANING UP